**CIFAR MODEL POISONED WITH DFST BACKDOOR ATTACK (SUNRISE HUE). RULES USED TO DETECT POISONED INPUTS AT RUNTIME AND GUESS THE CORRECT LABEL.**

In [ ]:
from google.colab import drive
#drive.mount('/content/drive')
#drive.flush_and_unmount()
#!rm -rf /content/drive

drive.mount('/content/drive', force_remount=True)

Mounted at /content/drive


In [ ]:
!pip install tf-keras-vis
# -*- coding: utf-8 -*-
"""GradCam.ipynb

Automatically generated by Colaboratory.

Original file is located at
    https://colab.research.google.com/drive/1cKjutZfO-CAwKnI4E84NAhm4seqoyGi0
"""

#!pip install tf-keras-vis

import tensorflow as tf
from tensorflow.keras import backend as K
import numpy as np
import time
#from Models.loss import smoothL1
from tensorflow.keras.models import Model
from tensorflow.keras.models import load_model
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, Dense, Dropout, Input, InputLayer
from tensorflow.keras.layers import Activation, Flatten, BatchNormalization
from tensorflow.keras.regularizers import l2

from tf_keras_vis.gradcam import Gradcam
from tf_keras_vis.gradcam import GradcamPlusPlus

from tf_keras_vis.utils import normalize

import matplotlib.pyplot as plt



import math
import io
import os
from collections import namedtuple
import sys

import operator

import copy

#from tf_keras_vis.utils import num_of_gpus

#_, gpus = num_of_gpus()
#print('{} GPUs'.format(gpus))
!pwd
os.chdir("./drive/MyDrive/Colab Notebooks")
!pwd
!ls

print(tf.__version__)

from platform import python_version

print(python_version())

/content
/content/drive/MyDrive/Colab Notebooks
 0_0.npy
 10_N_MNIST_GEN_SET_25_2.txt
 10_N_MNIST_GEN_SET_LABELS_25_2.txt
 25_N_CIFAR_GEN_SET_50_10.txt
 25_N_CIFAR_GEN_SET_LABELS_50_10.txt
'ACASX keras model.ipynb'
 ACASX_Prophecy.ipynb
'Anchor on tabular data.ipynb'
'Anchor SCENIC.ipynb'
'Backdoor DFST.ipynb'
 backdoor_test_X_cifar.txt
 backdoor_test_X_GTSRB.txt
 backdoor_test_X_MNIST.txt
'BoeingTaxiNet (1).ipynb'
 BoeingTaxiNet.ipynb
'Boeing TaxiNet Prophecy Runtime_v2.ipynb'
'Boeing TaxiNet Visualization (1).ipynb'
'Boeing TaxiNet Visualization.ipynb'
 BOEING_YOLO.ipynb
 cifar10b_sunrise.h5
 cifar10_normalization.h5
 cifar10-poisoned.hdf5
 cifar10_sunrise.h5
 CIFAR_GEN_SET_50_10.txt
 CIFAR_GEN_SET_LABELS_50_10.txt
 cifar.hdf5
 CIFAR-Original.ipynb
 cifar_test
 CIFAR_VAL_SET_50_10.txt
 CIFAR_VAL_SET_LABELS_50_10.txt
'Compare DNN-Coverage.ipynb'
'ConcolicNN 2.ipynb'
 config.py.ipynb
'ConstructTestSet1 (1).py'
'ConstructTestSet1 (2).py'
'ConstructTestSet1 (3).py'
'ConstructTestSet1 (4)

In [ ]:
import os
import keras
import argparse
import numpy as np
import tensorflow as tf
from keras.datasets import cifar10
from keras.preprocessing.image import ImageDataGenerator
#from keras.layers.normalization import BatchNormalization
from keras.layers import Conv2D, Dense, Input, add, Activation, GlobalAveragePooling2D
from keras.callbacks import LearningRateScheduler
from keras.models import Model, load_model
from keras import optimizers, regularizers
from keras import backend as K
import pickle

def get_prediction(img, tensor = None):

    if tensor == "ALL":
        full_list = []
        for tensor in ['dense_1', 'dense_2', 'dense_3']:
            layer_name = tensor
            layer = model.get_layer(layer_name)
            func = K.function(model.input, [layer.output])
            imag = np.expand_dims(img,axis=0)
            outputs = func(imag)
           # print(outputs)
            layer_outputs_test = []
            fingerprint1 = ((outputs[0] > 0.0).astype('int'))
            layer_outputs_test = []
            layer_result = fingerprint1
            layer_outputs_test.append(layer_result[0])
            full_list.append(layer_outputs_test)

        new_list = [list(full_list[0][0])+list(full_list[1][0])+list(full_list[2][0])]
        layer_outputs_test = np.asarray(new_list)
        return layer_outputs_test
    else:
        layer_name = tensor
        layer = model.get_layer(layer_name)
        func = K.function(model.input, [layer.output])
        imag = np.expand_dims(img,axis=0)
        outputs = func(imag)
       # print(outputs)
        fingerprint1 = ((outputs[0] > 0.0).astype('int'))
        layer_outputs_test = []
        layer_result = fingerprint1
        layer_outputs_test.append(layer_result[0])
        layer_outputs_test = np.asarray(layer_outputs_test)

        return layer_outputs_test

def get_prediction_vals(img, tensor = None):

    if tensor == "ALL":
        full_list = []
        for tensor in ['activation_1','activation_2','activation_3']:
            layer_name = tensor
            layer = model.get_layer(layer_name)
            func = K.function(model.input, [layer.output])
            imag = np.expand_dims(img,axis=0)
            outputs = func(imag)
            op = np.array(outputs)
            #print(op.shape)
            flat_op = op.flatten()
            #print(flat_op.shape)
            fingerprint1 = list(flat_op)
            #print(layer.name,fingerprint1)
            layer_outputs_test = []
            layer_result = fingerprint1
            layer_outputs_test.append(layer_result)
            full_list.append(layer_outputs_test)

        new_list = [list(full_list[0][0])+list(full_list[1][0])+list(full_list[2][0])]
        layer_outputs_test = np.asarray(new_list)
        return layer_outputs_test
    else:
        layer_name = tensor
        layer = model.get_layer(layer_name)
        func = K.function(model.input, [layer.output])
        imag = np.expand_dims(img,axis=0)
        outputs = func(imag)
       # print(outputs)
        #fingerprint1 = ((outputs[0] > 0.0).astype('int'))
        fingerprint1 = outputs[0]
        layer_outputs_test = []
        layer_result = fingerprint1
        layer_outputs_test.append(layer_result[0])
        layer_outputs_test = np.asarray(layer_outputs_test)

        return layer_outputs_test





def fingerprint_suffix(img,ten):
    return (get_prediction(img, tensor=ten)>0.0).astype('int')

def fingerprint_suffix_vals(img,ten):
    return get_prediction_vals(img, tensor=ten)

#from tf_keras_vis.gradcam import Gradcam
#from tf_keras_vis.gradcam import GradcamPlusPlus

def model_modifier_act1_layer(current_model):
    target_layer = current_model.get_layer(name='activation_1') #layer is the name of the intermediate layer
    new_model = tf.keras.Model(inputs=current_model.inputs,
                               outputs=target_layer.output)
    new_model.layers[-1].activation = tf.keras.activations.linear
    return new_model

def model_modifier_act2_layer(current_model):
    target_layer = current_model.get_layer(name='activation_2') #layer is the name of the intermediate layer
    new_model = tf.keras.Model(inputs=current_model.inputs,
                               outputs=target_layer.output)
    new_model.layers[-1].activation = tf.keras.activations.linear
    return new_model

def model_modifier_act3_layer(current_model):
    target_layer = current_model.get_layer(name='activation_3') #layer is the name of the intermediate layer
    new_model = tf.keras.Model(inputs=current_model.inputs,
                               outputs=target_layer.output)
    new_model.layers[-1].activation = tf.keras.activations.linear
    return new_model

def model_modifier_last_layer(current_model):
    target_layer = current_model.get_layer(name='activation_5') #layer is the name of the intermediate layer
    new_model = tf.keras.Model(inputs=current_model.inputs,
                               outputs=target_layer.output)
    new_model.layers[-1].activation = tf.keras.activations.linear
    return new_model

def model_modifier_layer(current_model):
    target_layer = current_model.get_layer(name='dense') #layer is the name of the intermediate layer
    new_model = tf.keras.Model(inputs=current_model.inputs,
                               outputs=target_layer.output)
    new_model.layers[-1].activation = tf.keras.activations.linear
    return new_model

def model_modifier_layer_inps(current_model):
    src_layer = current_model.get_layer(name='activation')
    target_layer = current_model.get_layer(name='dense') #layer is the name of the intermediate layer
    new_model = tf.keras.Model(inputs=src_layer.input,
                               outputs=target_layer.output)
    new_model.layers[-1].activation = tf.keras.activations.linear
    return new_model

def loss_gen_sum(node_list):
    def loss(output):
        print(output.shape)
        op = np.array(output)

        #if (op.ndim > 2):
        op = op.flatten()
        output = np.empty((1,len(op)))
        print(output.shape)
        output[0] = op

        loss_val = sum([output[0][i] for i in node_list])/len(node_list)
        return loss_val
    return loss


def loss_gen_sum1(node_list):
    def loss(output):

        loss_val = sum([output[0][i] for i in node_list])/len(node_list)
        return loss_val
    return loss

def loss_gen_sep(node):
    def loss(output):
        loss_val = output[0][node]
        return loss_val
    return loss

#import matplotlib.pyplot as plt
#from keras.models import load_model
print('Loading the model:')
model=load_model('cifar10b_sunrise.h5')#,custom_objects={'smoothL1':smoothL1})
print("Printing summary of the model:")
model.summary()

layer_name = 'dense'
lay = model.get_layer(layer_name)
print(lay.get_config())

layer_name = 'activation_4'
lay = model.get_layer(layer_name)
print(lay.get_config())






Loading the model:
Printing summary of the model:
Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 30, 30, 32)        896       
                                                                 
 activation (Activation)     (None, 30, 30, 32)        0         
                                                                 
 conv2d_1 (Conv2D)           (None, 28, 28, 32)        9248      
                                                                 
 activation_1 (Activation)   (None, 28, 28, 32)        0         
                                                                 
 max_pooling2d (MaxPooling2D  (None, 14, 14, 32)       0         
 )                                                               
                                                                 
 conv2d_2 (Conv2D)           (None, 12, 12, 64)        18496     
      

In [ ]:
def check_pattern(layer_vals,suff,neuron_ids,neuron_sig,VAL = False,ALL = False):
   #layer = 'activation_3'  #layer name, get it from the model summary
   #neuron_ids =  [-1,71,-1,20,-1,1,-1,28,-1,79,-1,29,-1,39,-1,49,-1,42,-1,33,-1,114,-1,117,-1,88,-1,31,-1,36,-1,33,-1,17,-1,117,-1,1,-1,28,-1,97] # neuron ids in the pattern
   #neuron_sig =  ['>',0.435630053,'>',4.067234278,'<=',42.78802872,'<=',20.19964218,'<=',41.11421585,'<=',23.87646389,'<=',15.27161694,'<=',36.27468491,'<=',30.84732342,'<=',40.63782883,'<=',25.80421829,'<=',43.16035843,'<=',38.44324303,'<=',66.91875458,'<=',26.18983078,'<=',16.70914364,'<=',41.36343193,'<=',35.72474098,'<=',35.5690403,'<=',14.66370487,'<=',40.59473419189453]

   if (VAL == False):
      if ((suff[:,neuron_ids][0] == neuron_sig).all(axis=0)):
        return True
      else:
        return False

   found = True;

   oper = -1
   for ind in range(0,len(neuron_ids)):
     if (ind % 2 == 0):
       op = neuron_sig[ind]
       if (op == '<='):
         oper = 0
       else:
         oper = 1
     else:
       v = int(neuron_ids[ind])
       vsig = float(neuron_sig[ind])
       val = layer_vals[v]
       #print(v,vsig,val,oper)
       if (oper == 0):
         if (val > vsig):
           found = False
           break
       else:
         if (val <= vsig):
            found = False
            break
       oper = -1

   return found

In [ ]:
import numpy as np
import csv

num_classes = 10

with open('cifar_test', 'rb') as f1:
    testset = pickle.load(f1, encoding='bytes')

x_test = testset['x_test']
y_test = testset['y_test']

ORIG_X = x_test

print ('Number of samples', len(y_test))
y_test = tf.keras.utils.to_categorical(y_test, num_classes)

print("== DONE! ==\n== COLOR PREPROCESSING... ==")
# color preprocessing
x_test = x_test.astype('float32')
mean = [125.307, 122.95, 113.865]
std = [62.9932, 62.0887, 66.7048]
for i in range(3):
    x_test[:, :, :, i] = (x_test[:, :, :, i] - mean[i]) / std[i]

testFULL_Y = (y_test).argmax(axis=1)
testFULL_X = x_test

#a=[]
#path = 'test_Y.txt'
#inputfile = csv.reader(open(path,'r')) # DEFINES THE INPUT FILE
#for row in inputfile: # TRAVERSES ALL ROWS OF DATA
#    c=[]
#    for i in range(0,len(row)):
#        c.append(int(row[i]))
#    a.append(c)
#test_Y = np.array(a)
print("IDEAL LABELS:", testFULL_Y.shape)

#a=[]
#path = 'test_X.txt'
#inputfile = csv.reader(open(path,'r')) # DEFINES THE INPUT FILE
#for row in inputfile: # TRAVERSES ALL ROWS OF DATA
#    c=[]
#    for i in range(0,len(row)):
#        c.append(int(row[i]))
#    c = np.reshape(c, (32,32,3))
#    a.append(c)
#test_X = np.array(a)
print("CLEAN DATA:", testFULL_X.shape)



test_labels = (model.predict(testFULL_X)).argmax(axis=1)
print("FULL TEST LABELS:", test_labels.shape)
PASS = 0
FAIL = 0
for indx in range(0, len(test_labels)):
  if (test_labels[indx] == testFULL_Y[indx]):
    PASS = PASS + 1
  else:
    FAIL = FAIL + 1
print("PASS:", PASS, ",FAIL:", FAIL, ",TEST ACCURACY:", (PASS/(PASS+FAIL))*100.0)


### RANDOM SPLIT INTO VAL AND TEST SET
import random
length = (len(testFULL_X))
ind = 0
valinds = []
while (ind < (length)/2):
  ix = random.randint(0,length)
  while(ix in valinds):
    ix = random.randint(0,length)
  valinds.append(ix)
  ind = ind + 1

test_X = []
test_Y = []
val_X = []
val_Y = []
for indx in range(0,length):
  if (indx in valinds):
    val_X.append(testFULL_X[indx])
    val_Y.append(testFULL_Y[indx])
  else:
    test_X.append(testFULL_X[indx])
    test_Y.append(testFULL_Y[indx])

val_X = np.array(val_X)
val_Y = np.array(val_Y)
test_X = np.array(test_X)
test_Y = np.array(test_Y)
print("VALIDATION SET:", len(val_X), val_X.shape, len(val_Y), val_Y.shape)
print("TEST SET:", len(test_X), test_X.shape, len(test_Y), test_Y.shape)

val_labels = (model.predict(val_X)).argmax(axis=1)
print("ACTUAL Val LABELS:", val_labels.shape)
PASS = 0
FAIL = 0
for indx in range(0, len(val_labels)):
  if (val_labels[indx] == val_Y[indx]):
    PASS = PASS + 1
  else:
    FAIL = FAIL + 1
print("PASS:", PASS, ",FAIL:", FAIL, ",VAL ACCURACY:", (PASS/(PASS+FAIL))*100.0)

test_labels = (model.predict(test_X)).argmax(axis=1)
print("ACTUAL TEST LABELS:", test_labels.shape)
PASS = 0
FAIL = 0
for indx in range(0, len(test_labels)):
  if (test_labels[indx] == test_Y[indx]):
    PASS = PASS + 1
  else:
    FAIL = FAIL + 1
print("PASS:", PASS, ",FAIL:", FAIL, ",TEST ACCURACY:", (PASS/(PASS+FAIL))*100.0)




gen_data = np.array(test_X)
gen_labels = np.array(test_Y)

gen_act_labels = (model.predict(gen_data)).argmax(axis=1)
print("ACTUAL GEN LABELS:", gen_act_labels.shape)

label0_tots = len(np.where(gen_act_labels == 0)[0])
label1_tots = len(np.where(gen_act_labels == 1)[0])
label2_tots = len(np.where(gen_act_labels == 2)[0])
label3_tots = len(np.where(gen_act_labels == 3)[0])
label4_tots = len(np.where(gen_act_labels == 4)[0])
label5_tots = len(np.where(gen_act_labels == 5)[0])
label6_tots = len(np.where(gen_act_labels == 6)[0])
label7_tots = len(np.where(gen_act_labels == 7)[0])
label8_tots = len(np.where(gen_act_labels == 8)[0])
label9_tots = len(np.where(gen_act_labels == 9)[0])

print(label0_tots,label1_tots,label2_tots,label3_tots,label4_tots,label5_tots)
print(label6_tots,label7_tots,label8_tots,label9_tots)

Pgen_data = []
Pgen_labels = []
PASS = 0
FAIL = 0
for indx in range(0, len(gen_labels)):
  Pgen_data.append(gen_data[indx])
  Pgen_labels.append(gen_labels[indx])
  if (gen_act_labels[indx] == gen_labels[indx]):
    PASS = PASS + 1
  else:
    FAIL = FAIL + 1
print("PASS:", PASS, ",FAIL:", FAIL, ",GEN ACCURACY:", (PASS/(PASS+FAIL))*100.0)

with open('sunrise_test_10000', 'rb') as f1:
    testset = pickle.load(f1, encoding='bytes')

x_test = testset['x_test']
y_test = testset['y_test']

POIS_ORIG_X = x_test

print ('Number of samples', len(y_test))
y_test = tf.keras.utils.to_categorical(y_test, num_classes)

print("== DONE! ==\n== COLOR PREPROCESSING... ==")
# color preprocessing
x_test = x_test.astype('float32')
mean = [125.307, 122.95, 113.865]
std = [62.9932, 62.0887, 66.7048]
for i in range(3):
    x_test[:, :, :, i] = (x_test[:, :, :, i] - mean[i]) / std[i]

poisoned_x = x_test
poisoned_Y = (y_test).argmax(axis=1)

#a=[]
#path = 'backdoor_test_X.txt'
#inputfile = csv.reader(open(path,'r')) # DEFINES THE INPUT FILE
#for row in inputfile: # TRAVERSES ALL ROWS OF DATA
#    c=[]
#    for i in range(0,len(row)):
#        c.append(int(row[i]))
#    c = np.reshape(c, (32,32,3))
#    a.append(c)
    #print(c)
    #print(c.shape)
#poisoned_x = np.array(a)
print("POISONED INPUTS:", poisoned_x.shape)
print("POSIONED_Y:", poisoned_Y.shape)

poisoned_labels = (model.predict(poisoned_x)).argmax(axis=1)
print("ACTUAL POISONED LABELS:", poisoned_labels.shape)
PASS = 0
FAIL = 0
for indx in range(0, len(poisoned_labels)):
  #print(poisoned_labels[indx])
  if (poisoned_labels[indx] == testFULL_Y[indx]):
    PASS = PASS + 1
  else:
    FAIL = FAIL + 1
print("PASS:", PASS, ",FAIL:", FAIL, ",POISONED ACCURACY:", (PASS/(PASS+FAIL))*100.0)

### RANDOM POISON DATA SPLIT INTO VAL AND TEST SET
import random
val_length = int((len(poisoned_x)) * (1/2))
ind = 0
valinds = []
while (ind < val_length):
  ix = random.randint(0,val_length)
  while(ix in valinds):
    ix = random.randint(0,val_length)
  valinds.append(ix)
  ind = ind + 1


Pval_X = []
Pval_Y = []
PTEST_X = []
PTEST_Y = []
for indx in range(0,len(poisoned_x)):
  if (indx in valinds):
    Pval_X.append(poisoned_x[indx])
    Pval_Y.append(testFULL_Y[indx])
  else:
    PTEST_X.append(poisoned_x[indx])
    PTEST_Y.append(testFULL_Y[indx])

Pval_X = np.array(Pval_X)
Pval_Y = np.array(Pval_Y)
print("VALIDATION SET:", len(Pval_X), Pval_X.shape, len(Pval_Y), Pval_Y.shape)


Pval_labels = (model.predict(Pval_X)).argmax(axis=1)
print("ACTUAL Val LABELS:", Pval_labels.shape)
PASS = 0
FAIL = 0
for indx in range(0, len(Pval_labels)):
  if (Pval_labels[indx] == Pval_Y[indx]):
    PASS = PASS + 1
  else:
    FAIL = FAIL + 1
print("PASS:", PASS, ",FAIL:", FAIL, ",PVAL ACCURACY:", (PASS/(PASS+FAIL))*100.0)

################################################################################

SPLIT = (5.0/100.0)
import random
test_length = int((len(PTEST_X)) * SPLIT)
ind = 0
testinds = []
while (ind < test_length):
  ix = random.randint(0,test_length)
  while(ix in testinds):
    ix = random.randint(0,test_length)
  testinds.append(ix)
  ind = ind + 1

Ptest_X = []
Ptest_Y = []
for indx in range(0,len(PTEST_X)):
  if (indx in testinds):
    Ptest_X.append(PTEST_X[indx])
    Ptest_Y.append(PTEST_Y[indx])


Ptest_X = np.array(Ptest_X)
Ptest_Y = np.array(Ptest_Y)
print("TEST SET:", len(Ptest_X), Ptest_X.shape, len(Ptest_Y), Ptest_Y.shape)


Ptest_labels = (model.predict(Ptest_X)).argmax(axis=1)
print("ACTUAL TEST LABELS:", Ptest_labels.shape)

PASS = 0
FAIL = 0
for indx in range(0, len(Ptest_labels)):
  Pgen_data.append(Ptest_X[indx])
  Pgen_labels.append(Ptest_Y[indx])
  if (Ptest_labels[indx] == Ptest_Y[indx]):
    PASS = PASS + 1
  else:
    FAIL = FAIL + 1
print("PASS:", PASS, ",FAIL:", FAIL, ",PTEST ACCURACY:", (PASS/(PASS+FAIL))*100.0)

Pgen_data = np.array(Pgen_data)
Pgen_labels = np.array(Pgen_labels)
print("Pgen", Pgen_data.shape, Pgen_labels.shape )
Pgen_act_labels = (model.predict(Pgen_data)).argmax(axis=1)
print("ACTUAL GEN LABELS:", Pgen_act_labels.shape)

PASS = 0
FAIL = 0
for indx in range(0, len(Pgen_labels)):
  if (Pgen_act_labels[indx] == Pgen_labels[indx]):
    PASS = PASS + 1
  else:
    FAIL = FAIL + 1
print("PASS:", PASS, ",FAIL:", FAIL, ",PGEN ACCURACY:", (PASS/(PASS+FAIL))*100.0)




Number of samples 10000
== DONE! ==
== COLOR PREPROCESSING... ==
IDEAL LABELS: (10000,)
CLEAN DATA: (10000, 32, 32, 3)
FULL TEST LABELS: (10000,)
PASS: 8170 ,FAIL: 1830 ,TEST ACCURACY: 81.69999999999999
VALIDATION SET: 4999 (4999, 32, 32, 3) 4999 (4999,)
TEST SET: 5001 (5001, 32, 32, 3) 5001 (5001,)
ACTUAL Val LABELS: (4999,)
PASS: 4071 ,FAIL: 928 ,VAL ACCURACY: 81.43628725745148
ACTUAL TEST LABELS: (5001,)
PASS: 4099 ,FAIL: 902 ,TEST ACCURACY: 81.96360727854429
ACTUAL GEN LABELS: (5001,)
557 490 469 434 508 469
603 486 495 490
PASS: 4099 ,FAIL: 902 ,GEN ACCURACY: 81.96360727854429
Number of samples 10000
== DONE! ==
== COLOR PREPROCESSING... ==
POISONED INPUTS: (10000, 32, 32, 3)
POSIONED_Y: (10000,)
ACTUAL POISONED LABELS: (10000,)
PASS: 1012 ,FAIL: 8988 ,POISONED ACCURACY: 10.12
VALIDATION SET: 5000 (5000, 32, 32, 3) 5000 (5000,)
ACTUAL Val LABELS: (5000,)
PASS: 497 ,FAIL: 4503 ,PVAL ACCURACY: 9.94
TEST SET: 250 (250, 32, 32, 3) 250 (250,)
ACTUAL TEST LABELS: (250,)
PASS: 27 ,FAIL: 

In [ ]:
#COLLECTING DATA FOR DECISION TREE LEARNING
import time
extract_pat_start_time = time.time()

layer = model.get_layer('dense') # activation, activation_2, activation_3, activation_4, activation_5
func = K.function(model.input, [layer.output])
outputs = func(gen_data)
fingerprint_1 = ((outputs[0] > 0.0).astype('int'))
fingerprint1 = outputs[0]

layer = model.get_layer('activation_4') # activation, activation_2, activation_3, activation_4, activation_5
func = K.function(model.input, [layer.output])
outputs = func(gen_data)
fingerprint_2 = ((outputs[0] > 0.0).astype('int'))
fingerprint2 = outputs[0]





PASS = 0
FAIL = 0
val_vec1 = []
val_vec_labels1 = []
actuals_gen = (model.predict(gen_data)).argmax(axis=1)
print("VALS from layer:")
for i in range(0,len(fingerprint1)):
  #print(actuals_gen[i],gen_labels[i])
  if (actuals_gen[i] == gen_labels[i]):
    PASS = PASS + 1
    val_vec_labels1.append(gen_labels[i])
    val_vec1.append(np.asarray((fingerprint1[i]).flatten()))
  else:
    FAIL = FAIL + 1
    val_vec_labels1.append(10 + actuals_gen[i])
    val_vec1.append(np.asarray((fingerprint1[i]).flatten()))

PASS = 0
FAIL = 0
act_vec1 = []
act_vec_labels1 = []
print("ACT from layer:")
for i in range(0,len(fingerprint_1)):
  if (actuals_gen[i] == gen_labels[i]):
    PASS = PASS + 1
    act_vec_labels1.append(gen_labels[i])
    act_vec1.append(np.asarray((fingerprint_1[i]).flatten()))
  else:
    FAIL = FAIL + 1
    act_vec_labels1.append(10 + actuals_gen[i])
    act_vec1.append(np.asarray((fingerprint_1[i]).flatten()))

PASS = 0
FAIL = 0
val_vec2 = []
val_vec_labels2 = []
actuals_gen = (model.predict(gen_data)).argmax(axis=1)
print("VALS from layer:")
for i in range(0,len(fingerprint2)):
  if (actuals_gen[i] == gen_labels[i]):
    PASS = PASS + 1
    val_vec_labels2.append(gen_labels[i])
    val_vec2.append(np.asarray((fingerprint2[i]).flatten()))
  else:
    FAIL = FAIL + 1
    val_vec_labels2.append(10 + actuals_gen[i])
    val_vec2.append(np.asarray((fingerprint2[i]).flatten()))

PASS = 0
FAIL = 0
act_vec2 = []
act_vec_labels2 = []
print("ACT from layer:")
for i in range(0,len(fingerprint_2)):
  if (actuals_gen[i] == gen_labels[i]):
    PASS = PASS + 1
    act_vec_labels2.append(gen_labels[i])
    act_vec2.append(np.asarray((fingerprint_2[i]).flatten()))
  else:
    FAIL = FAIL + 1
    act_vec_labels2.append(10 + actuals_gen[i])
    act_vec2.append(np.asarray((fingerprint_2[i]).flatten()))


print("PASS:", PASS, ", FAIL:", FAIL, ",ACC:", ((PASS/(PASS+FAIL)) * 100.0))


VALS from layer:
ACT from layer:
VALS from layer:
ACT from layer:
PASS: 4099 , FAIL: 902 ,ACC: 81.96360727854429


In [ ]:
#layer_preds
layer = model.get_layer('dense') # activation, activation_2, activation_3, activation_4, activation_5
func = K.function(model.input, [layer.output])
outputs = func(Pgen_data)
Pfingerprint_1 = ((outputs[0] > 0.0).astype('int'))
Pfingerprint1 = outputs[0]

layer = model.get_layer('activation_4') # activation, activation_2, activation_3, activation_4, activation_5
func = K.function(model.input, [layer.output])
outputs = func(Pgen_data)
Pfingerprint_2 = ((outputs[0] > 0.0).astype('int'))
Pfingerprint2 = outputs[0]





PASS = 0
FAIL = 0
FAIL_P = 0
Pval_vec1 = []
Pval_vec_labels1 = []
actuals_gen = (model.predict(Pgen_data)).argmax(axis=1)
print("VALS from layer:")
for i in range(0,len(Pfingerprint1)):
  #print(actuals_gen[i],gen_labels[i])
  if (actuals_gen[i] == Pgen_labels[i]):
    PASS = PASS + 1
    Pval_vec_labels1.append(Pgen_labels[i])
    Pval_vec1.append(np.asarray((Pfingerprint1[i]).flatten()))
  else:
    FAIL = FAIL + 1
    if (actuals_gen[i] == 0):
      FAIL_P = FAIL_P + 1
      Pval_vec_labels1.append(1000)
    else:
      Pval_vec_labels1.append(10 + actuals_gen[i])
    Pval_vec1.append(np.asarray((Pfingerprint1[i]).flatten()))

PASS = 0
FAIL = 0
Pact_vec1 = []
Pact_vec_labels1 = []
print("ACT from layer:")
for i in range(0,len(Pfingerprint_1)):
  if (actuals_gen[i] == Pgen_labels[i]):
    PASS = PASS + 1
    Pact_vec_labels1.append(Pgen_labels[i])
    Pact_vec1.append(np.asarray((Pfingerprint_1[i]).flatten()))
  else:
    FAIL = FAIL + 1
    if (actuals_gen[i] == 0):
      Pact_vec_labels1.append(1000)
    else:
      Pact_vec_labels1.append(10 + actuals_gen[i])
    Pact_vec1.append(np.asarray((Pfingerprint_1[i]).flatten()))

PASS = 0
FAIL = 0
Pval_vec2 = []
Pval_vec_labels2 = []
actuals_gen = (model.predict(Pgen_data)).argmax(axis=1)
print("VALS from layer:")
for i in range(0,len(Pfingerprint2)):
  if (actuals_gen[i] == Pgen_labels[i]):
    PASS = PASS + 1
    Pval_vec_labels2.append(Pgen_labels[i])
    Pval_vec2.append(np.asarray((Pfingerprint2[i]).flatten()))
  else:
    FAIL = FAIL + 1
    if (actuals_gen[i] == 0):
      Pval_vec_labels2.append(1000)
    else:
      Pval_vec_labels2.append(10 + actuals_gen[i])
    Pval_vec2.append(np.asarray((Pfingerprint2[i]).flatten()))

PASS = 0
FAIL = 0
Pact_vec2 = []
Pact_vec_labels2 = []
print("ACT from layer:")
for i in range(0,len(Pfingerprint_2)):
  if (actuals_gen[i] == Pgen_labels[i]):
    PASS = PASS + 1
    Pact_vec_labels2.append(Pgen_labels[i])
    Pact_vec2.append(np.asarray((Pfingerprint_2[i]).flatten()))
  else:
    FAIL = FAIL + 1
    if (actuals_gen[i] == 0):
      Pact_vec_labels2.append(1000)
    else:
      Pact_vec_labels2.append(10 + actuals_gen[i])
    Pact_vec2.append(np.asarray((Pfingerprint_2[i]).flatten()))


print("PASS:", PASS, ", FAIL:", FAIL, ",ACC:", ((PASS/(PASS+FAIL)) * 100.0))
print(", FAIL POISONED:", FAIL_P)


VALS from layer:
ACT from layer:
VALS from layer:
ACT from layer:
PASS: 4126 , FAIL: 1125 ,ACC: 78.57550942677585
, FAIL POISONED: 330


In [ ]:
#layer_preds
layer = model.get_layer('dense') # activation, activation_2, activation_3, activation_4, activation_5
func = K.function(model.input, [layer.output])
outputs = func(Pgen_data)
Rfingerprint_1 = ((outputs[0] > 0.0).astype('int'))
Rfingerprint1 = outputs[0]

layer = model.get_layer('activation_4') # activation, activation_2, activation_3, activation_4, activation_5
func = K.function(model.input, [layer.output])
outputs = func(Pgen_data)
Rfingerprint_2 = ((outputs[0] > 0.0).astype('int'))
Rfingerprint2 = outputs[0]





PASS = 0
FAIL = 0
FAIL_P = 0
Rval_vec1 = []
Rval_vec_labels1 = []
actuals_gen = (model.predict(Pgen_data)).argmax(axis=1)
print("VALS from layer:")
for i in range(0,len(Rfingerprint1)):
  #print(actuals_gen[i],gen_labels[i])
  if (actuals_gen[i] == Pgen_labels[i]):
    PASS = PASS + 1
    Rval_vec_labels1.append(Pgen_labels[i])
    Rval_vec1.append(np.asarray((Rfingerprint1[i]).flatten()))
  else:
    FAIL = FAIL + 1
    if (actuals_gen[i] == 0):
      FAIL_P = FAIL_P + 1
      Rval_vec_labels1.append(Pgen_labels[i])
    else:
      Rval_vec_labels1.append(10 + actuals_gen[i])
    Rval_vec1.append(np.asarray((Rfingerprint1[i]).flatten()))

PASS = 0
FAIL = 0
Ract_vec1 = []
Ract_vec_labels1 = []
print("ACT from layer:")
for i in range(0,len(Rfingerprint_1)):
  if (actuals_gen[i] == Pgen_labels[i]):
    PASS = PASS + 1
    Ract_vec_labels1.append(Pgen_labels[i])
    Ract_vec1.append(np.asarray((Rfingerprint_1[i]).flatten()))
  else:
    FAIL = FAIL + 1
    if (actuals_gen[i] == 0):
      Ract_vec_labels1.append(Pgen_labels[i])
    else:
      Ract_vec_labels1.append(10 + actuals_gen[i])
    Ract_vec1.append(np.asarray((Rfingerprint_1[i]).flatten()))

PASS = 0
FAIL = 0
Rval_vec2 = []
Rval_vec_labels2 = []
actuals_gen = (model.predict(Pgen_data)).argmax(axis=1)
print("VALS from layer:")
for i in range(0,len(Rfingerprint2)):
  if (actuals_gen[i] == Pgen_labels[i]):
    PASS = PASS + 1
    Rval_vec_labels2.append(Pgen_labels[i])
    Rval_vec2.append(np.asarray((Rfingerprint2[i]).flatten()))
  else:
    FAIL = FAIL + 1
    if (actuals_gen[i] == 0):
      Rval_vec_labels2.append(Pgen_labels[i])
    else:
      Rval_vec_labels2.append(10 + actuals_gen[i])
    Rval_vec2.append(np.asarray((Rfingerprint2[i]).flatten()))

PASS = 0
FAIL = 0
Ract_vec2 = []
Ract_vec_labels2 = []
print("ACT from layer:")
for i in range(0,len(Rfingerprint_2)):
  if (actuals_gen[i] == Pgen_labels[i]):
    PASS = PASS + 1
    Ract_vec_labels2.append(Pgen_labels[i])
    Ract_vec2.append(np.asarray((Rfingerprint_2[i]).flatten()))
  else:
    FAIL = FAIL + 1
    if (actuals_gen[i] == 0):
      Ract_vec_labels2.append(Pgen_labels[i])
    else:
      Ract_vec_labels2.append(10 + actuals_gen[i])
    Ract_vec2.append(np.asarray((Rfingerprint_2[i]).flatten()))


print("PASS:", PASS, ", FAIL:", FAIL, ",ACC:", ((PASS/(PASS+FAIL)) * 100.0))
print(", FAIL POISONED:", FAIL_P)


VALS from layer:
ACT from layer:
VALS from layer:
ACT from layer:
PASS: 4126 , FAIL: 1125 ,ACC: 78.57550942677585
, FAIL POISONED: 330


In [ ]:
from sklearn import tree

val_vec1 = np.asarray(val_vec1)
val_vec_labels1 = np.asarray(val_vec_labels1)
print(val_vec1.shape, val_vec_labels1.shape)
## PATTERNs WITH ACTUAL LABELS
basic_estimator1 = tree.DecisionTreeClassifier()
basic_estimator1.fit(val_vec1, val_vec_labels1)

act_vec1 = np.asarray(act_vec1)
act_vec_labels1 = np.asarray(act_vec_labels1)
print(act_vec1.shape, act_vec_labels1.shape)
## PATTERNs WITH ACTUAL LABELS
basic_estimator1a = tree.DecisionTreeClassifier()
basic_estimator1a.fit(act_vec1, act_vec_labels1)

val_vec2 = np.asarray(val_vec2)
val_vec_labels2 = np.asarray(val_vec_labels2)
print(val_vec2.shape, val_vec_labels2.shape)
basic_estimator2 = tree.DecisionTreeClassifier()
basic_estimator2.fit(val_vec2, val_vec_labels2)

act_vec2 = np.asarray(act_vec2)
act_vec_labels2 = np.asarray(act_vec_labels2)
print(act_vec2.shape, act_vec_labels2.shape)
## PATTERNs WITH ACTUAL LABELS
basic_estimator2a = tree.DecisionTreeClassifier()
basic_estimator2a.fit(act_vec2, act_vec_labels2)

#extract_pat_time = time.time() - extract_pat_start_time

print("Patterns Extraction Time:", extract_pat_time)


(5001, 512) (5001,)
(5001, 512) (5001,)
(5001, 512) (5001,)
(5001, 512) (5001,)


DecisionTreeClassifier()

In [ ]:
from sklearn import tree

Pval_vec1 = np.asarray(Pval_vec1)
Pval_vec_labels1 = np.asarray(Pval_vec_labels1)
print(Pval_vec1.shape, Pval_vec_labels1.shape)
## PATTERNs WITH ACTUAL LABELS
Pbasic_estimator1 = tree.DecisionTreeClassifier()
Pbasic_estimator1.fit(Pval_vec1, Pval_vec_labels1)

Pact_vec1 = np.asarray(Pact_vec1)
Pact_vec_labels1 = np.asarray(Pact_vec_labels1)
print(Pact_vec1.shape, Pact_vec_labels1.shape)
## PATTERNs WITH ACTUAL LABELS
Pbasic_estimator1a = tree.DecisionTreeClassifier()
Pbasic_estimator1a.fit(Pact_vec1, Pact_vec_labels1)

Pval_vec2 = np.asarray(Pval_vec2)
Pval_vec_labels2 = np.asarray(Pval_vec_labels2)
print(Pval_vec2.shape, Pval_vec_labels2.shape)
Pbasic_estimator2 = tree.DecisionTreeClassifier()
Pbasic_estimator2.fit(Pval_vec2, Pval_vec_labels2)

Pact_vec2 = np.asarray(Pact_vec2)
Pact_vec_labels2 = np.asarray(Pact_vec_labels2)
print(Pact_vec2.shape, Pact_vec_labels2.shape)
## PATTERNs WITH ACTUAL LABELS
Pbasic_estimator2a = tree.DecisionTreeClassifier()
Pbasic_estimator2a.fit(Pact_vec2, Pact_vec_labels2)




(5251, 512) (5251,)
(5251, 512) (5251,)
(5251, 512) (5251,)
(5251, 512) (5251,)


DecisionTreeClassifier()

In [ ]:
from sklearn import tree

Rval_vec1 = np.asarray(Rval_vec1)
Rval_vec_labels1 = np.asarray(Rval_vec_labels1)
print(Rval_vec1.shape, Rval_vec_labels1.shape)
## PATTERNs WITH ACTUAL LABELS
Rbasic_estimator1 = tree.DecisionTreeClassifier()
Rbasic_estimator1.fit(Rval_vec1, Rval_vec_labels1)

Ract_vec1 = np.asarray(Ract_vec1)
Ract_vec_labels1 = np.asarray(Ract_vec_labels1)
print(Ract_vec1.shape, Ract_vec_labels1.shape)
## PATTERNs WITH ACTUAL LABELS
Rbasic_estimator1a = tree.DecisionTreeClassifier()
Rbasic_estimator1a.fit(Ract_vec1, Ract_vec_labels1)

Rval_vec2 = np.asarray(Rval_vec2)
Rval_vec_labels2 = np.asarray(Rval_vec_labels2)
print(Rval_vec2.shape, Rval_vec_labels2.shape)
Rbasic_estimator2 = tree.DecisionTreeClassifier()
Rbasic_estimator2.fit(Rval_vec2, Rval_vec_labels2)

Ract_vec2 = np.asarray(Ract_vec2)
Ract_vec_labels2 = np.asarray(Ract_vec_labels2)
print(Ract_vec2.shape, Ract_vec_labels2.shape)
## PATTERNs WITH ACTUAL LABELS
Rbasic_estimator2a = tree.DecisionTreeClassifier()
Rbasic_estimator2a.fit(Ract_vec2, Ract_vec_labels2)

extract_pat_time = time.time() - extract_pat_start_time

print("Patterns Extraction Time:", extract_pat_time)

(5251, 512) (5251,)
(5251, 512) (5251,)
(5251, 512) (5251,)
(5251, 512) (5251,)
Patterns Extraction Time: 78.84668064117432


In [ ]:
from tqdm import tqdm
import operator
import pandas as pd

train_suffixes = act_vec1
train_labels = act_vec_labels1

def get_decision_path(estimator, inp):
  # Extract the decision path taken by an input as an ordered list of indices
  # of the neurons that were evaluated.
  # See: http://scikit-learn.org/stable/auto_examples/tree/plot_unveil_tree_structure.html
  n_nodes = estimator.tree_.node_count
  feature = estimator.tree_.feature

  # First let's retrieve the decision path of each sample. The decision_path
  # method allows to retrieve the node indicator functions. A non zero element of
  # indicator matrix at the position (i, j) indicates that the sample i goes
  # through the node j.
  X_test = [inp]
  node_indicator = estimator.decision_path(X_test)
  # Similarly, we can also have the leaves ids reached by each sample.
  leaf_id = estimator.apply(X_test)
  # Now, it's possible to get the tests that were used to predict a sample or
  # a group of samples. First, let's make it for the sample.
  node_index = node_indicator.indices[node_indicator.indptr[0]:
                                      node_indicator.indptr[1]]
  neuron_ids = []
  for node_id in node_index:
    if leaf_id[0] == node_id:
        continue
    neuron_ids.append(feature[node_id])
  return neuron_ids

def get_suffix_cluster(neuron_ids, neuron_sig,suffixes=train_suffixes):
  # Get the cluster of inputs that such that all inputs in the cluster
  # have provided on/off signature for the provided neurons.
  #
  # The returned cluster is an array of indices (into mnist.train.images).
  return np.where((suffixes[:, neuron_ids] == neuron_sig).all(axis=1))[0]

def is_consistent_cluster(cluster, predictions):
  # Check if all inputs within the cluster have the same prediction.
  # 'cluster' is an array of input ids.
  pred = predictions[cluster[0]]
  for i in cluster:
    if predictions[i] != pred:
      return False
  return True



def get_invariant_inp(estimator, ref_id, suffixes):
  # Returns an invariant found w.r.t. the provided reference input
  # Args
  #  - inp: reference input, shape <784,>
  # Returns:
  #  - cluster: Indices of training inputs that satisfy the invariant
  #  - neuron_id: A list of neurons such that all inputs that agree with
  #    the reference input on the on/off status of these neurons have the
  #    same prediction as the reference input.
  ref_img = mnist_inp_images[ref_id]
  ref_suffix = suffixes[ref_id]
  print('PREFIX',ref_suffix)
  neuron_ids = get_decision_path(estimator, ref_suffix)
  print('NEURON IDS',neuron_ids)
  neuron_sig = ref_suffix[neuron_ids]
  print('NEURON SIGNATURE',neuron_sig)
  cluster = get_suffix_cluster(neuron_ids, neuron_sig,suffixes)
  imgs = []
  cnt = 0
  for indx1 in range(0,len(cluster)):
    img = mnist.train.images(cluster[indx1])
    fnd = 1
    for i in range(0,len(img)):
      if (ref_img[i] != img[i]):
        fnd = 0
        break
    if (fnd == 1):
        ref_id = cnt
    cnt = cnt + 1
    imgs.append(img)

  imgs_suffixes = fingerprint_signature(imgs,t_fc2)
  ref_suffix = imgs_suffixes[ref_id]
  print('PREFIX',ref_suffix)
  neuron_ids = get_decision_path(estimator, ref_suffix)
  print('NEURON IDS',neuron_ids)
  neuron_sig = ref_suffix[neuron_ids]
  print('NEURON SIGNATURE',neuron_sig)
  cluster = get_suffix_cluster(neuron_ids, neuron_sig,imgs_suffixes)

  return cluster, neuron_ids, neuron_sig

def get_invariant(estimator, ref_id):
  # Returns an invariant found w.r.t. the provided reference input
  # Args
  #  - ref_id: Index (into mnist.train.images) of the reference input
  # Returns:
  #  - cluster: Indices of training inputs that satisfy the invariant
  #  - neuron_id: A list of neurons such that all inputs that agree with
  #    the reference input on the on/off status of these neurons have the
  #    same prediction as the reference input.
  ref_img = mnist.train.images[ref_id]
  ref_suffix = train_suffixes[ref_id]
  neuron_ids = get_decision_path(estimator, ref_suffix)
  neuron_sig = ref_suffix[neuron_ids]
  cluster = get_suffix_cluster(neuron_ids, neuron_sig)
  return cluster, neuron_ids, neuron_sig


def get_all_invariants(estimator):
  # Returns a dictionary mapping each decision tree prediction class
  # to a list of invariants. Each invariant is specified as a triple:
  # - neuron ids
  # - neuron signature (for the neuron ids)
  # - number of training samples that hit it
  # The neuron ids and neuron signature can be supplied to get_suffix_cluster
  # to obtain the cluster of training instances that hit the invariant.
  def is_leaf(node):
    return estimator.tree_.children_left[node] == estimator.tree_.children_right[node]

  def left_child(node):
    return estimator.tree_.children_left[node]

  def right_child(node):
    return estimator.tree_.children_right[node]

  def get_all_paths_rec(node):
    # Returns a list of triples corresponding to paths
    # in the decision tree. Each triple consists of
    # - neurons encountered along the path
    # - signature along the path
    # - prediction class at the leaf
    # - number of training samples that hit the path
    # The prediction class and number of training samples
    # are set to -1 when the leaf is "impure".
    feature = estimator.tree_.feature
    threshold = estimator.tree_.threshold
    if is_leaf(node):
      values = estimator.tree_.value[node][0]
      if len(np.where(values != 0)[0]) == 1:
        cl = estimator.classes_[np.where(values != 0)[0][0]]
        nsamples = estimator.tree_.n_node_samples[node]
      else:
        # impure node
        cl = -1
        nsamples = -1
      return [[[], [], cl, nsamples]]
    # If it is not a leaf both left and right childs must exist
   # paths = [[[feature[node]] + p[0], [0] + p[1], p[2], p[3]] for p in get_all_paths_rec(left_child(node))]
   # paths += [[[feature[node]] + p[0], [1] + p[1], p[2], p[3]] for p in get_all_paths_rec(right_child(node))]
    paths = [[[feature[node]] + p[0],['<='] + [threshold[node]] + p[1], p[2], p[3]] for p in get_all_paths_rec(left_child(node))]
    paths += [[[feature[node]] + p[0],['>'] + [threshold[node]] + p[1], p[2], p[3]] for p in get_all_paths_rec(right_child(node))]
    return paths
  paths =  get_all_paths_rec(0)
  print("Obtained all paths")
  invariants = {}
  for p in tqdm(paths):
    neuron_ids, neuron_sig, cl, nsamples = p
    if cl not in invariants:
      invariants[cl] = []
    # cluster = get_suffix_cluster(neuron_ids, neuron_sig)
    invariants[cl].append([neuron_ids, neuron_sig, nsamples])
  for cl in invariants.keys():
    invariants[cl] = sorted(invariants[cl], key=operator.itemgetter(2), reverse=True)
  return invariants


def describe_cluster(cluster, neuron_ids, show_samples=False):
  neuron_sig = train_suffixes[cluster[0]][neuron_ids]
  print("Num neurons in invariant", len(neuron_ids))
  print("Neuron id and signature")

  for i in range(0,len(neuron_ids)):
    print("id:", neuron_ids[i], "sig:", neuron_sig[i])

  print("Cluster size: ", len(cluster))
  print("Num misclassified", len([i for i in cluster if is_misclassified(i)]))
  if show_samples:
    for i in range(10):
      images = []
      for j in range(10):
        if 10*i + j >= len(cluster):
          break
        images.append(mnist_to_pil_img(mnist.train.images[cluster[10*i+j]]))
      if len(images) > 0:
        show_img(combine(images))

def describe_invariants_all_labels_col(all_invariants,suffixes=train_suffixes,COMMON=False, DEC_PREFX= False):
  invs_sel_neus = []
  invs_sel_sig = []
  Minvs_sel_neus = []
  Minvs_sel_sig = []
  Minvs_sel_supp = []
  invs_sel_supp = []
  invs_sel_cl = []
  Minvs_sel_cl = []

  corr_invs_sel_labs = []
  corr_invs_sel_neus = []
  corr_invs_sel_sig = []
  corr_invs_sel_supp = []

  for cl, invs in all_invariants.items():

    for indx in range (0, len(invs)):
      inv = invs[indx]


     # print("Class:", cl, ", Rule:(neurons:",inv[0],",signature:",inv[1],"),Support:",inv[2])

    # MISCLASSIFICATION PATTTERN FOR IDEAL LABELs
      if (cl == 1000):
          Minvs_sel_cl.append(cl)
          Minvs_sel_neus.append(inv[0])
          Minvs_sel_sig.append(inv[1])
          Minvs_sel_supp.append(inv[2])

      # MISCLASSIFICATION PATTTERNs FOR ACTUAL LABELS
      if (cl >= 10):
        invs_sel_neus.append(inv[0])
        invs_sel_sig.append(inv[1])
        invs_sel_supp.append(inv[2])
        invs_sel_cl.append(cl)


      #if ((cl >= 0) ): #and (cl not in corr_invs_sel_labs)):
      if ((cl >= 0) and (cl < 10)):
          corr_invs_sel_labs.append(cl)
          corr_invs_sel_neus.append(inv[0])
          corr_invs_sel_sig.append(inv[1])
          corr_invs_sel_supp.append(inv[2])



  return (Minvs_sel_neus, Minvs_sel_sig, Minvs_sel_supp, Minvs_sel_cl, invs_sel_neus, invs_sel_sig, invs_sel_supp, invs_sel_cl, corr_invs_sel_labs, corr_invs_sel_neus, corr_invs_sel_sig, corr_invs_sel_supp)


def describe_invariants_all_labels(all_invariants,suffixes=train_suffixes,COMMON=False, DEC_PREFX= False):
  invs_sel_neus = []
  invs_sel_sig = []
  invs_sel_supp = []
  corr_invs_sel_labs = []
  corr_invs_sel_neus = []
  corr_invs_sel_sig = []
  corr_invs_sel_supp = []

 # print("PRINTING PURE RULES WITH SUPPORT MORE THAN 100 FOR EVERY LABEL:");
  supp = 0
  for cl, invs in all_invariants.items():

    for indx in range (0, len(invs)):
      inv = invs[indx]
      if (inv[2] <= 10):
        continue
      #print("Class:", cl, ", Rule:(neurons:",inv[0],",signature:",inv[1],"),Support:",inv[2])
      print("Class:", cl, "Support:",inv[2])
      if (cl == -1000):
        if (inv[2] > ((10/100) * FAIL_P)):
          invs_sel_neus.append(inv[0])
          invs_sel_sig.append(inv[1])
          invs_sel_supp.append(inv[2])
          supp = supp + inv[2]

      if ((cl >= 0) and (cl not in corr_invs_sel_labs)):
          corr_invs_sel_labs.append(cl)
          corr_invs_sel_neus.append(inv[0])
          corr_invs_sel_sig.append(inv[1])
          corr_invs_sel_supp.append(inv[2])

      continue

      cls = get_suffix_cluster(inv[0],inv[1],suffixes)

      neurons = inv[0]
      signature = inv[1]

      if (len(cls) <= 10):
         continue

     # fail_cnt = []
     # fail_label = []
     # pass_cnt = []
     # for ind in range(0,len(cls)):
     #   inp_indx = cls[ind]
     #   if (FP[inp_indx] == 0):
     #     fail_cnt.append(inp_indx)
     #     fail_label.append(IDEAL[inp_indx])
     #   else:
     #     pass_cnt.append(inp_indx)

      #fail_perc = (fail_cnt/len(cls))
      #if (inv[2] == 243):
      #print("Class:", cl, ", Rule:(neurons:",inv[0],",signature:",inv[1],"),Support:",inv[2],",Pass:",[i for i in pass_cnt],",Mis:",[i for i in fail_cnt] , ",Label:",[i for i in fail_label]);

      print("Class:", cl, ", Rule:(neurons:",inv[0],",signature:",inv[1],"),Support:",inv[2])
      #if (indx > 0):
      #  break
     # for ind in range(0, len(cls)):
     #    print(cls[ind])

     # break
      if (COMMON == True):
          common_nodes(cls,suffixes)

      if (DEC_PREFX == True):
          decision_prefs(cls,suffixes)

  return (invs_sel_neus, invs_sel_sig, invs_sel_supp, corr_invs_sel_labs, corr_invs_sel_neus, corr_invs_sel_sig, corr_invs_sel_supp)


def common_nodes(cls,suffixes):
    cnt = 0
    common = np.zeros(10,dtype=int)
    prev = np.zeros(10,dtype=int)

    for indx in range(0, len(cls)):
        i = cls[indx]
        cnt = cnt + 1
        for j in range(0,len(suffixes[i])):
          if (common[j] == -1):
             continue
          if ((indx != 0) and (suffixes[i][j] != prev[j])):
             common[j] = -1
          else:
             common[j] = suffixes[i][j]
          prev[j] = suffixes[i][j]


    print('COMMON NODES IN CLUSTER for CLASS:',cl,cnt)
    com = []
    for k in range(0,len(common)):
        if (common[k] != -1):
           com.append((k,common[k]))
    print(com)

    return

def decision_prefs(cls,suffixes):
    images = mnist.train.images
    imgsCom = []
    imgs = []
    for indx in range(0, len(cls)):
        print('IMG:')
        print(list(zip(images[cls[indx]])))
        imgs.append(images[cls[indx]])
        imgsCom.append(images[cls[indx]])

    dec_prefixes= fingerprint_signature(imgs,layer)
    prefixes = []
    for indx in range(0,len(dec_prefixes)):
       dec_pref = dec_prefixes[indx]

       match = 0
       for indx1 in range(0, len(prefixes)):
          match = 1
          for i in range(0,len(prefixes[indx1])):
             if (dec_pref[i] != prefixes[indx1][i]):
                match = 0
                break
          if (match == 1):
             break

       if (match == 0):
          prefixes.append(dec_pref)

    print('DECISION PREFIXES IN CLUSTER for CLASS:',cl,cnt)
    for k in range(0,len(prefixes)):
      print(prefixes[k])

    return


In [ ]:
#invariants = get_all_invariants(basic_estimator)
#(Ainvs_sel_neus, Ainvs_sel_sig, Ainvs_sel_supp, Acorr_invs_sel_labs, Acorr_invs_sel_neus, Acorr_invs_sel_sig, Acorr_invs_sel_supp) = describe_invariants_all_labels(invariants)
#print("ACTIVATION PATTERNS:")
#for indx in range(0, len(Ainvs_sel_neus)):
#  print(Ainvs_sel_neus[indx], Ainvs_sel_sig[indx], Ainvs_sel_supp[indx])
#for indx in range(0, len(Acorr_invs_sel_labs)):
#  print(Acorr_invs_sel_labs[indx], Acorr_invs_sel_neus[indx], Acorr_invs_sel_sig[indx], Acorr_invs_sel_supp[indx])


#invariants = get_all_invariants(basic_estimator1)
#(invs_sel_neus, invs_sel_sig, invs_sel_supp, corr_invs_sel_labs, corr_invs_sel_neus, corr_invs_sel_sig, corr_invs_sel_supp) = describe_invariants_all_labels(invariants)

corr_invs_sel_lay1 = []
corr_invs_sel_lay1a = []
corr_invs_sel_lay2 = []
corr_invs_sel_lay2a = []
corr_invs_sel_lay3 = []
corr_invs_sel_lay3a = []

invariants_VAL1 = get_all_invariants(basic_estimator1)
(Minvs_sel_neus1, Minvs_sel_sig1, Minvs_sel_sup1, Minvs_sel_cl1,invs_sel_neus, invs_sel_sig, invs_sel_supp, invs_sel_cl, corr_invs_sel_labs1, corr_invs_sel_neus1, corr_invs_sel_sig1, corr_invs_sel_supp1) = describe_invariants_all_labels_col(invariants_VAL1)

print("\n CORRECT PATTERNS VAL 1:\n")
for indx in range(0, len(corr_invs_sel_neus1)):
   corr_invs_sel_lay1.append(1)
   print(corr_invs_sel_labs1[indx], corr_invs_sel_neus1[indx], corr_invs_sel_sig1[indx], corr_invs_sel_supp1[indx])

invariants_ACT1 = get_all_invariants(basic_estimator1a)
(Minvs_sel_neus1, Minvs_sel_sig1, Minvs_sel_sup1, Minvs_sel_cl1,invs_sel_neus, invs_sel_sig, invs_sel_supp, invs_sel_cl, corr_invs_sel_labs1a, corr_invs_sel_neus1a, corr_invs_sel_sig1a, corr_invs_sel_supp1a) = describe_invariants_all_labels_col(invariants_ACT1)

print("\n CORRECT PATTERNS ACT 1:\n")
for indx in range(0, len(corr_invs_sel_neus1a)):
   corr_invs_sel_lay1a.append(1)
   print(corr_invs_sel_labs1a[indx], corr_invs_sel_neus1a[indx], corr_invs_sel_sig1a[indx], corr_invs_sel_supp1a[indx])


invariants_VAL2 = get_all_invariants(basic_estimator2)
(Minvs_sel_neus1, Minvs_sel_sig1, Minvs_sel_sup1, Minvs_sel_cl1,invs_sel_neus, invs_sel_sig, invs_sel_supp, invs_sel_cl, corr_invs_sel_labs2, corr_invs_sel_neus2, corr_invs_sel_sig2, corr_invs_sel_supp2) = describe_invariants_all_labels_col(invariants_VAL2)

print("\n CORRECT PATTERNS VAL 2:\n")
for indx in range(0, len(corr_invs_sel_neus2)):
   corr_invs_sel_lay2.append(2)
   print(corr_invs_sel_labs2[indx], corr_invs_sel_neus2[indx], corr_invs_sel_sig2[indx], corr_invs_sel_supp2[indx])

invariants_ACT2 = get_all_invariants(basic_estimator2a)
(Minvs_sel_neus1, Minvs_sel_sig1, Minvs_sel_sup1, Minvs_sel_cl1,invs_sel_neus, invs_sel_sig, invs_sel_supp, invs_sel_cl, corr_invs_sel_labs2a, corr_invs_sel_neus2a, corr_invs_sel_sig2a, corr_invs_sel_supp2a) = describe_invariants_all_labels_col(invariants_ACT2)

print("\n CORRECT PATTERNS ACT 2:\n")
for indx in range(0, len(corr_invs_sel_neus2a)):
   corr_invs_sel_lay2a.append(2)
   print(corr_invs_sel_labs2a[indx], corr_invs_sel_neus2a[indx], corr_invs_sel_sig2a[indx], corr_invs_sel_supp2a[indx])


Obtained all paths


100%|██████████| 1189/1189 [00:00<00:00, 404102.38it/s]


 CORRECT PATTERNS VAL 1:

6 [441, 25, 207, 125, 154, 463, 209, 229, 407, 275, 149] ['<=', 10.604980945587158, '<=', 6.657510280609131, '>', 8.957874298095703, '<=', -16.855595588684082, '<=', -5.255013465881348, '<=', -24.0157470703125, '<=', 7.276564598083496, '<=', -9.76518440246582, '<=', -10.05820083618164, '<=', 1.8192381262779236, '<=', -12.581329822540283] 169
6 [441, 25, 207, 125, 154, 463, 126, 490, 203, 213, 480] ['<=', 10.604980945587158, '<=', 6.657510280609131, '>', 8.957874298095703, '<=', -16.855595588684082, '<=', -5.255013465881348, '>', -24.0157470703125, '>', -18.59367275238037, '<=', -12.193171977996826, '<=', -12.288246154785156, '<=', -4.40836226940155, '<=', -14.406616687774658] 61
6 [441, 25, 207, 76, 297, 501, 407, 206, 302, 262, 287, 224, 222, 216, 188, 385, 275, 32] ['<=', 10.604980945587158, '<=', 6.657510280609131, '<=', 8.957874298095703, '<=', -10.26868724822998, '>', -31.959747314453125, '<=', 4.710258722305298, '<=', -2.0271835327148438, '<=', -1.52644

2 [441, 25, 207, 76, 297, 501, 407, 206, 288, 206, 276, 175, 349, 333, 125, 323, 266, 446, 190] ['<=', 10.604980945587158, '<=', 6.657510280609131, '<=', 8.957874298095703, '<=', -10.26868724822998, '>', -31.959747314453125, '<=', 4.710258722305298, '<=', -2.0271835327148438, '>', -1.5264425873756409, '>', -9.501451015472412, '<=', 8.02124285697937, '<=', -9.214542388916016, '>', -9.813645362854004, '<=', -0.8210462331771851, '<=', -6.55090594291687, '<=', -2.262208342552185, '>', -25.02165126800537, '>', -23.570960998535156, '<=', -26.53216552734375, '>', -11.078768730163574] 1
2 [441, 25, 207, 76, 297, 501, 407, 206, 288, 206, 194, 483, 381, 215, 45] ['<=', 10.604980945587158, '<=', 6.657510280609131, '<=', 8.957874298095703, '<=', -10.26868724822998, '>', -31.959747314453125, '<=', 4.710258722305298, '<=', -2.0271835327148438, '>', -1.5264425873756409, '>', -9.501451015472412, '>', 8.02124285697937, '<=', -10.274849891662598, '<=', -4.247802972793579, '<=', 12.723050117492676, '>', 

100%|██████████| 1651/1651 [00:00<00:00, 736994.03it/s]

...


 CORRECT PATTERNS VAL 2:

2 [441, 25, 207, 389, 92, 501, 407, 206, 11, 262, 209, 144, 408, 285, 440, 332, 188, 224, 375, 260, 276, 164, 10, 469, 2, 6, 225] ['<=', 10.604980945587158, '<=', 6.657510280609131, '<=', 8.957874298095703, '<=', 0.8254246115684509, '<=', 1.9773771166801453, '<=', 0.1877131164073944, '<=', 2.40395188331604, '<=', 0.008085265755653381, '<=', 2.4103026390075684, '<=', 3.0880775451660156, '<=', 6.214353799819946, '>', 4.471221923828125, '<=', 0.07667074352502823, '<=', 0.9195168614387512, '<=', 1.7849936485290527, '<=', 3.71156108379364, '<=', 2.6550974249839783, '<=', 5.664328098297119, '<=', 6.843840599060059, '<=', 7.928158760070801, '<=', 3.5818254947662354, '<=', 13.271622657775879, '<=', 14.386683940887451, '<=', 6.823814868927002, '<=', 1.2449904084205627, '<=', 5.373858451843262, '<=', 12.376298904418945] 76
2 [441, 25, 207, 389, 92, 501, 407, 206, 11, 262, 209, 252, 233, 442, 223, 267, 311, 419] ['<=', 10.604980945587158, '<=', 6.657510280609131, '<=', 

 1
7 [441, 25, 207, 207, 137, 440, 487, 206, 307, 255, 440, 359, 105, 452, 410, 252, 7, 507, 340, 452, 376, 10, 106, 391, 212] ['<=', 10.604980945587158, '<=', 6.657510280609131, '>', 8.957874298095703, '<=', 15.508479118347168, '<=', 1.1588343381881714, '<=', 10.54923152923584, '<=', 0.07592859864234924, '<=', 6.2920379638671875, '<=', 1.7783247232437134, '<=', 12.536099433898926, '<=', 2.4499588012695312, '<=', 4.447397470474243, '<=', 0.9030049443244934, '<=', 6.878058671951294, '<=', 2.5027726888656616, '<=', 1.128322035074234, '<=', 1.2286429405212402, '<=', 5.189309358596802, '<=', 2.0454803705215454, '<=', 1.9818847179412842, '<=', 0.5887135863304138, '<=', 0.13671258091926575, '<=', 1.6188403367996216, '>', 0.12386241555213928, '>', 2.1141853034496307] 1
7 [441, 25, 207, 207, 137, 440, 487, 206, 307, 255, 440, 359, 105, 452, 410, 252, 7, 507, 141, 392] ['<=', 10.604980945587158, '<=', 6.657510280609131, '>', 8.957874298095703, '<=', 15.508479118347168, '<=', 1.1588343381881714,

100%|██████████| 1655/1655 [00:00<00:00, 574443.32it/s]


 CORRECT PATTERNS ACT 2:

3 [441, 207, 0, 501, 407, 11, 389, 206, 8, 146, 408, 424, 233, 25, 294, 226, 262, 337, 327, 365, 410, 181, 267, 452, 14] ['<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5] 30
3 [441, 207, 206, 288, 230, 262, 410, 212, 122, 204, 55, 400, 175] ['<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5] 21
3 [441, 207, 0, 501, 407, 11, 389, 206, 8, 146, 408, 424, 233, 25, 294, 226, 262, 127, 484, 380, 24, 277, 199, 349, 333, 492] ['<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=',

2 [441, 207, 206, 288, 440, 410, 91, 487, 141, 162, 256, 103, 167, 255, 335, 28, 276] ['<=', 0.5, '>', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5] 2
2 [441, 207, 206, 288, 440, 489, 230, 216, 192, 197, 215, 153, 52] ['<=', 0.5, '>', 0.5, '<=', 0.5, '>', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5] 2
2 [441, 207, 206, 288, 440, 489, 230, 216, 192, 197, 215, 423] ['<=', 0.5, '>', 0.5, '<=', 0.5, '>', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5] 2
2 [441, 207, 206, 288, 440, 489, 230, 316, 145] ['<=', 0.5, '>', 0.5, '<=', 0.5, '>', 0.5, '>', 0.5, '<=', 0.5, '>', 0.5, '>', 0.5, '>', 0.5] 2
2 [441, 207, 206, 353, 468, 7, 452, 465, 180, 111, 156, 56] ['<=', 0.5, '>', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '>', 0.5, '<

In [ ]:
#invariants = get_all_invariants(basic_estimator)
#(Ainvs_sel_neus, Ainvs_sel_sig, Ainvs_sel_supp, Acorr_invs_sel_labs, Acorr_invs_sel_neus, Acorr_invs_sel_sig, Acorr_invs_sel_supp) = describe_invariants_all_labels(invariants)
#print("ACTIVATION PATTERNS:")
#for indx in range(0, len(Ainvs_sel_neus)):
#  print(Ainvs_sel_neus[indx], Ainvs_sel_sig[indx], Ainvs_sel_supp[indx])
#for indx in range(0, len(Acorr_invs_sel_labs)):
#  print(Acorr_invs_sel_labs[indx], Acorr_invs_sel_neus[indx], Acorr_invs_sel_sig[indx], Acorr_invs_sel_supp[indx])


#invariants = get_all_invariants(basic_estimator1)
#(invs_sel_neus, invs_sel_sig, invs_sel_supp, corr_invs_sel_labs, corr_invs_sel_neus, corr_invs_sel_sig, corr_invs_sel_supp) = describe_invariants_all_labels(invariants)

Rcorr_invs_sel_lay1 = []
Rcorr_invs_sel_lay1a = []
Rcorr_invs_sel_lay2 = []
Rcorr_invs_sel_lay2a = []
Rcorr_invs_sel_lay3 = []
Rcorr_invs_sel_lay3a = []

Rinvariants_VAL1 = get_all_invariants(Rbasic_estimator1)
(Minvs_sel_neus1, Minvs_sel_sig1, Minvs_sel_sup1, Minvs_sel_cl1,invs_sel_neus, invs_sel_sig, invs_sel_supp, invs_sel_cl, Rcorr_invs_sel_labs1, Rcorr_invs_sel_neus1, Rcorr_invs_sel_sig1, Rcorr_invs_sel_supp1) = describe_invariants_all_labels_col(Rinvariants_VAL1)

print("\n CORRECT PATTERNS VAL 1:\n")
for indx in range(0, len(Rcorr_invs_sel_neus1)):
   Rcorr_invs_sel_lay1.append(1)
   print(Rcorr_invs_sel_labs1[indx], Rcorr_invs_sel_neus1[indx], Rcorr_invs_sel_sig1[indx], Rcorr_invs_sel_supp1[indx])

Rinvariants_ACT1 = get_all_invariants(Rbasic_estimator1a)
(Minvs_sel_neus1, Minvs_sel_sig1, Minvs_sel_sup1, Minvs_sel_cl1,invs_sel_neus, invs_sel_sig, invs_sel_supp, invs_sel_cl, Rcorr_invs_sel_labs1a, Rcorr_invs_sel_neus1a, Rcorr_invs_sel_sig1a, Rcorr_invs_sel_supp1a) = describe_invariants_all_labels_col(Rinvariants_ACT1)

print("\n CORRECT PATTERNS ACT 1:\n")
for indx in range(0, len(Rcorr_invs_sel_neus1a)):
   Rcorr_invs_sel_lay1a.append(1)
   print(Rcorr_invs_sel_labs1a[indx], Rcorr_invs_sel_neus1a[indx], Rcorr_invs_sel_sig1a[indx], Rcorr_invs_sel_supp1a[indx])


Rinvariants_VAL2 = get_all_invariants(Rbasic_estimator2)
(Minvs_sel_neus1, Minvs_sel_sig1, Minvs_sel_sup1, Minvs_sel_cl1,invs_sel_neus, invs_sel_sig, invs_sel_supp, invs_sel_cl, Rcorr_invs_sel_labs2, Rcorr_invs_sel_neus2, Rcorr_invs_sel_sig2, Rcorr_invs_sel_supp2) = describe_invariants_all_labels_col(Rinvariants_VAL2)

print("\n CORRECT PATTERNS VAL 2:\n")
for indx in range(0, len(Rcorr_invs_sel_neus2)):
   Rcorr_invs_sel_lay2.append(2)
   print(Rcorr_invs_sel_labs2[indx], Rcorr_invs_sel_neus2[indx], Rcorr_invs_sel_sig2[indx], Rcorr_invs_sel_supp2[indx])

Rinvariants_ACT2 = get_all_invariants(Rbasic_estimator2a)
(Minvs_sel_neus1, Minvs_sel_sig1, Minvs_sel_sup1, Minvs_sel_cl1,invs_sel_neus, invs_sel_sig, invs_sel_supp, invs_sel_cl, Rcorr_invs_sel_labs2a, Rcorr_invs_sel_neus2a, Rcorr_invs_sel_sig2a, Rcorr_invs_sel_supp2a) = describe_invariants_all_labels_col(Rinvariants_ACT2)

print("\n CORRECT PATTERNS ACT 2:\n")
for indx in range(0, len(Rcorr_invs_sel_neus2a)):
   Rcorr_invs_sel_lay2a.append(2)
   print(Rcorr_invs_sel_labs2a[indx], Rcorr_invs_sel_neus2a[indx], Rcorr_invs_sel_sig2a[indx], Rcorr_invs_sel_supp2a[indx])


Obtained all paths


100%|██████████| 1278/1278 [00:00<00:00, 172779.80it/s]


 CORRECT PATTERNS VAL 1:

6 [441, 25, 207, 125, 154, 463, 209, 229, 407, 353, 220] ['<=', 10.604980945587158, '<=', 5.930540084838867, '>', 8.957874298095703, '<=', -16.855595588684082, '<=', -5.255013465881348, '<=', -24.0157470703125, '<=', 7.276564598083496, '<=', -9.76518440246582, '<=', -10.05820083618164, '<=', -7.861505508422852, '<=', 2.9854349493980408] 167
6 [441, 25, 207, 125, 154, 463, 126, 490, 203, 213, 480] ['<=', 10.604980945587158, '<=', 5.930540084838867, '>', 8.957874298095703, '<=', -16.855595588684082, '<=', -5.255013465881348, '>', -24.0157470703125, '>', -18.59367275238037, '<=', -12.193171977996826, '<=', -12.288246154785156, '<=', -4.40836226940155, '<=', -14.406616687774658] 61
6 [441, 25, 207, 125, 5, 307, 105, 222, 198, 363, 151, 149, 494] ['<=', 10.604980945587158, '<=', 5.930540084838867, '>', 8.957874298095703, '>', -16.855595588684082, '<=', -7.082141876220703, '<=', 2.3072811365127563, '<=', -4.325988054275513, '<=', -21.598970413208008, '<=', -22.8656

 ['<=', 10.604980945587158, '<=', 5.930540084838867, '<=', 8.957874298095703, '<=', -10.263668537139893, '>', -31.959747314453125, '<=', 4.710258722305298, '>', -2.0271835327148438, '<=', 5.696076154708862, '<=', -24.400229454040527, '<=', 1.8306259512901306, '<=', -6.765532970428467, '<=', -10.648662567138672, '>', -35.426151275634766, '<=', -3.250741124153137, '<=', -36.794057846069336, '>', -20.70289134979248, '<=', -21.08598232269287, '<=', -38.81629943847656] 1
7 [441, 25, 207, 76, 297, 501, 407, 233, 400, 187, 4, 64, 424, 496, 310, 381, 98] ['<=', 10.604980945587158, '<=', 5.930540084838867, '<=', 8.957874298095703, '<=', -10.263668537139893, '>', -31.959747314453125, '<=', 4.710258722305298, '>', -2.0271835327148438, '<=', 5.696076154708862, '<=', -24.400229454040527, '<=', 1.8306259512901306, '<=', -6.765532970428467, '<=', -10.648662567138672, '>', -35.426151275634766, '<=', -3.250741124153137, '>', -36.794057846069336, '<=', 6.051031827926636, '>', 3.378397226333618] 1
7 [441

100%|██████████| 1750/1750 [00:00<00:00, 120086.25it/s]

...


 CORRECT PATTERNS VAL 2:

3 [441, 25, 207, 389, 92, 501, 407, 206, 11, 262, 335, 262, 172, 230, 233, 408] ['<=', 10.604980945587158, '<=', 5.930540084838867, '<=', 8.957874298095703, '<=', 0.8254246115684509, '<=', 1.9773771166801453, '<=', 0.1877131164073944, '<=', 2.40395188331604, '<=', 0.008085265755653381, '<=', 2.4103026390075684, '>', 3.0880775451660156, '<=', 15.797532081604004, '>', 5.830905437469482, '<=', 17.673499584197998, '<=', 1.898323118686676, '<=', 2.217052698135376, '<=', 13.021985054016113] 58
3 [441, 25, 207, 389, 92, 501, 407, 206, 11, 262, 209, 144, 163, 233, 442, 259, 484, 255, 474, 485, 148, 408, 340, 48] ['<=', 10.604980945587158, '<=', 5.930540084838867, '<=', 8.957874298095703, '<=', 0.8254246115684509, '<=', 1.9773771166801453, '<=', 0.1877131164073944, '<=', 2.40395188331604, '<=', 0.008085265755653381, '<=', 2.4103026390075684, '<=', 3.0880775451660156, '<=', 6.214353799819946, '<=', 4.471221923828125, '<=', 7.043302059173584, '<=', 9.08201551437378, '<=

 [441, 25, 207, 389, 92, 501, 407, 206, 11, 262, 209, 144, 163, 233, 442, 259, 484, 255, 474, 485, 148, 36, 226, 419, 342, 364, 330, 192, 67, 160, 453, 252, 273, 290, 153] ['<=', 10.604980945587158, '<=', 5.930540084838867, '<=', 8.957874298095703, '<=', 0.8254246115684509, '<=', 1.9773771166801453, '<=', 0.1877131164073944, '<=', 2.40395188331604, '<=', 0.008085265755653381, '<=', 2.4103026390075684, '<=', 3.0880775451660156, '<=', 6.214353799819946, '<=', 4.471221923828125, '<=', 7.043302059173584, '<=', 9.08201551437378, '<=', 1.5570796728134155, '<=', 3.654170513153076, '<=', 0.01747274398803711, '<=', 7.0666351318359375, '<=', 2.2502533197402954, '<=', 0.10558951646089554, '<=', 3.6518176794052124, '<=', 4.285862684249878, '<=', 0.116839949041605, '<=', 11.366937160491943, '<=', 0.5501210689544678, '<=', 0.7884052395820618, '>', 1.7126702070236206, '<=', 0.7712402939796448, '<=', 1.2760674953460693, '<=', 0.9861957877874374, '<=', 1.3535161018371582, '<=', 8.683187365531921, '<=',

100%|██████████| 1756/1756 [00:00<00:00, 273565.27it/s]


 CORRECT PATTERNS ACT 2:

3 [441, 207, 25, 389, 501, 407, 290, 146, 233, 262, 307, 331, 198, 65, 410] ['<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5] 35
3 [441, 207, 206, 288, 230, 262, 410, 212, 225, 204, 449, 411, 175] ['<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5] 21
3 [441, 207, 25, 389, 501, 407, 290, 146, 233, 262, 200, 424, 408, 202, 185, 206, 505, 3, 253, 375, 380, 366, 17, 455, 374, 19, 255, 409, 34, 210] ['<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5] 10
3 [441, 207, 25, 389, 501, 407, 290, 

[441, 1, 61, 25, 491, 51, 207, 353, 461, 54, 262, 370, 206, 499, 231, 45, 356, 307, 208, 236, 119, 12, 190, 141, 152, 155, 311, 339, 366, 440] ['>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5] 1
2 [441, 1, 61, 25, 491, 51, 207, 353, 461, 54, 262, 370, 206, 499, 231, 45, 356, 307, 228, 135, 215] ['>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '>', 0.5, '>', 0.5] 1
2 [441, 1, 61, 25, 491, 51, 207, 353, 461, 54, 262, 370, 206, 394, 102, 85, 41] ['>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 

In [ ]:
#invariants = get_all_invariants(basic_estimator)
#(Ainvs_sel_neus, Ainvs_sel_sig, Ainvs_sel_supp, Acorr_invs_sel_labs, Acorr_invs_sel_neus, Acorr_invs_sel_sig, Acorr_invs_sel_supp) = describe_invariants_all_labels(invariants)
#print("ACTIVATION PATTERNS:")
#for indx in range(0, len(Ainvs_sel_neus)):
#  print(Ainvs_sel_neus[indx], Ainvs_sel_sig[indx], Ainvs_sel_supp[indx])
#for indx in range(0, len(Acorr_invs_sel_labs)):
#  print(Acorr_invs_sel_labs[indx], Acorr_invs_sel_neus[indx], Acorr_invs_sel_sig[indx], Acorr_invs_sel_supp[indx])


#invariants = get_all_invariants(basic_estimator1)
#(invs_sel_neus, invs_sel_sig, invs_sel_supp, corr_invs_sel_labs, corr_invs_sel_neus, corr_invs_sel_sig, corr_invs_sel_supp) = describe_invariants_all_labels(invariants)

Pcorr_invs_sel_lay1 = []
Pcorr_invs_sel_lay1a = []
Pcorr_invs_sel_lay2 = []
Pcorr_invs_sel_lay2a = []
PMinvs_sel_lay1 = []
PMinvs_sel_lay1a = []
PMinvs_sel_lay2 = []
PMinvs_sel_lay2a = []

Pinvariants_VAL1 = get_all_invariants(Pbasic_estimator1)
(PMinvs_sel_neus1, PMinvs_sel_sig1, PMinvs_sel_sup1, PMinvs_sel_cl1,Pinvs_sel_neus, Pinvs_sel_sig, Pinvs_sel_supp, Pinvs_sel_cl, Pcorr_invs_sel_labs1, Pcorr_invs_sel_neus1, Pcorr_invs_sel_sig1, Pcorr_invs_sel_supp1) = describe_invariants_all_labels_col(Pinvariants_VAL1)

print("\n CORRECT PATTERNS VAL 1:\n")
for indx in range(0, len(Pcorr_invs_sel_neus1)):
   Pcorr_invs_sel_lay1.append(1)
   print(Pcorr_invs_sel_labs1[indx], Pcorr_invs_sel_neus1[indx], Pcorr_invs_sel_sig1[indx], Pcorr_invs_sel_supp1[indx])

print("\n MISCLASS PATTERNS VAL 1:\n")
for indx in range(0, len(PMinvs_sel_neus1)):
   PMinvs_sel_lay1.append(1)
   print(PMinvs_sel_cl1[indx], PMinvs_sel_neus1[indx], PMinvs_sel_sig1[indx], PMinvs_sel_sup1[indx])

Pinvariants_ACT1 = get_all_invariants(Pbasic_estimator1a)
(PMinvs_sel_neus1a, PMinvs_sel_sig1a, PMinvs_sel_sup1a, PMinvs_sel_cl1a,Pinvs_sel_neus1a, Pinvs_sel_sig1a, Pinvs_sel_supp1a, Pinvs_sel_cl1a, Pcorr_invs_sel_labs1a, Pcorr_invs_sel_neus1a, Pcorr_invs_sel_sig1a, Pcorr_invs_sel_supp1a) = describe_invariants_all_labels_col(Pinvariants_ACT1)

print("\n CORRECT PATTERNS ACT 1:\n")
for indx in range(0, len(Pcorr_invs_sel_neus1a)):
   Pcorr_invs_sel_lay1a.append(1)
   print(Pcorr_invs_sel_labs1a[indx], Pcorr_invs_sel_neus1a[indx], Pcorr_invs_sel_sig1a[indx], Pcorr_invs_sel_supp1a[indx])

print("\n MISCLASS PATTERNS ACT 1:\n")
for indx in range(0, len(PMinvs_sel_neus1a)):
   PMinvs_sel_lay1a.append(1)
   print(PMinvs_sel_cl1a[indx], PMinvs_sel_neus1a[indx], PMinvs_sel_sig1a[indx], PMinvs_sel_sup1a[indx])


Pinvariants_VAL2 = get_all_invariants(Pbasic_estimator2)
(PMinvs_sel_neus2, PMinvs_sel_sig2, PMinvs_sel_sup2, PMinvs_sel_cl2,invs_sel_neus, Pinvs_sel_sig, Pinvs_sel_supp,Pinvs_sel_cl, Pcorr_invs_sel_labs2, Pcorr_invs_sel_neus2, Pcorr_invs_sel_sig2, Pcorr_invs_sel_supp2) = describe_invariants_all_labels_col(Pinvariants_VAL2)

print("\n CORRECT PATTERNS VAL 2:\n")
for indx in range(0, len(Pcorr_invs_sel_neus2)):
   Pcorr_invs_sel_lay2.append(2)
   print(Pcorr_invs_sel_labs2[indx], Pcorr_invs_sel_neus2[indx], Pcorr_invs_sel_sig2[indx], Pcorr_invs_sel_supp2[indx])

print("\n MISCLASS PATTERNS VAL 2:\n")
for indx in range(0, len(PMinvs_sel_neus2)):
   PMinvs_sel_lay2.append(2)
   print(PMinvs_sel_cl2[indx], PMinvs_sel_neus2[indx], PMinvs_sel_sig2[indx], PMinvs_sel_sup2[indx])

Pinvariants_ACT2 = get_all_invariants(Pbasic_estimator2a)
(PMinvs_sel_neus2a, PMinvs_sel_sig2a, PMinvs_sel_sup2a, PMinvs_sel_cl2a,invs_sel_neus, Pinvs_sel_sig, Pinvs_sel_supp, Pinvs_sel_cl, Pcorr_invs_sel_labs2a, Pcorr_invs_sel_neus2a, Pcorr_invs_sel_sig2a, Pcorr_invs_sel_supp2a) = describe_invariants_all_labels_col(Pinvariants_ACT2)

print("\n CORRECT PATTERNS ACT 2:\n")
for indx in range(0, len(Pcorr_invs_sel_neus2a)):
   Pcorr_invs_sel_lay2a.append(2)
   print(Pcorr_invs_sel_labs2a[indx], Pcorr_invs_sel_neus2a[indx], Pcorr_invs_sel_sig2a[indx], Pcorr_invs_sel_supp2a[indx])

print("\n MISCLASS PATTERNS ACT 2:\n")
for indx in range(0, len(PMinvs_sel_neus2a)):
   PMinvs_sel_lay2a.append(2)
   print(PMinvs_sel_cl2a[indx], PMinvs_sel_neus2a[indx], PMinvs_sel_sig2a[indx], PMinvs_sel_sup2a[indx])


Obtained all paths


100%|██████████| 1210/1210 [00:00<00:00, 153035.25it/s]


 CORRECT PATTERNS VAL 1:

8 [441, 509, 25, 327, 168, 278, 50, 457, 38, 139, 36, 180, 510, 373, 425, 226, 403, 440, 356] ['<=', 10.604980945587158, '<=', 6.190656900405884, '>', 6.657510280609131, '<=', -21.011231422424316, '<=', -3.3187501430511475, '>', -14.2793550491333, '<=', 6.879307508468628, '<=', 6.491411209106445, '<=', 2.3189245462417603, '<=', 0.7343689799308777, '<=', -4.431285262107849, '<=', -7.106683015823364, '<=', 5.110281944274902, '<=', -6.230676174163818, '<=', 2.325345993041992, '<=', 14.165750980377197, '<=', -4.1809810400009155, '<=', 8.132670879364014, '<=', 13.35473108291626] 235
8 [441, 509, 25, 207, 76, 234, 415, 447, 81] ['<=', 10.604980945587158, '<=', 6.190656900405884, '<=', 6.657510280609131, '<=', 8.957874298095703, '>', -10.26868724822998, '>', -0.9866737127304077, '<=', -6.2064268589019775, '<=', -4.706621885299683, '>', -33.98086166381836] 35
8 [441, 509, 25, 207, 76, 297, 501, 407, 206, 302, 424, 233, 8, 0, 502, 169] ['<=', 10.604980945587158, '<=',

0 [441, 509, 25, 207, 76, 297, 501, 407, 206, 302, 262, 287, 224, 222, 416, 404, 506, 446, 307, 380, 16, 409, 291, 64, 509, 371, 186, 345, 454, 130, 148, 360, 295, 172, 340, 366, 234] ['<=', 10.604980945587158, '<=', 6.190656900405884, '<=', 6.657510280609131, '<=', 8.957874298095703, '<=', -10.26868724822998, '>', -31.959747314453125, '<=', 4.710258722305298, '<=', -2.0271835327148438, '<=', -1.5264425873756409, '>', -14.407398223876953, '<=', 5.650258779525757, '<=', -5.858856201171875, '<=', -3.0951476097106934, '>', -22.796271324157715, '>', -28.306900024414062, '<=', 1.0926052629947662, '<=', -3.9407012462615967, '<=', 5.526860237121582, '<=', 2.1023067235946655, '<=', 0.14891121163964272, '<=', 1.088856279850006, '<=', 4.668482065200806, '<=', 0.11977094039320946, '<=', -8.72074556350708, '<=', -17.506505966186523, '<=', -8.70129108428955, '<=', 4.681782484054565, '<=', 7.343597888946533, '<=', -13.293361186981201, '>', -14.639552116394043, '>', -13.20845890045166, '<=', -10.6764

100%|██████████| 1678/1678 [00:00<00:00, 83358.51it/s]

...


 CORRECT PATTERNS VAL 2:

3 [441, 355, 25, 207, 389, 92, 501, 407, 206, 11, 262, 335, 262, 172, 230, 408, 19] ['<=', 10.604980945587158, '<=', 1.1936511918902397, '<=', 6.657510280609131, '<=', 8.957874298095703, '<=', 0.8254246115684509, '<=', 1.9773771166801453, '<=', 0.1877131164073944, '<=', 2.40395188331604, '<=', 0.008085265755653381, '<=', 2.4103026390075684, '>', 3.0880775451660156, '<=', 15.797532081604004, '>', 5.830905437469482, '<=', 17.673499584197998, '<=', 1.898323118686676, '<=', 13.021985054016113, '<=', 0.46517854928970337] 58
3 [441, 355, 25, 207, 389, 92, 501, 407, 206, 11, 262, 209, 144, 163, 233, 442, 259, 484, 255, 474, 224, 375, 148, 408, 169, 137] ['<=', 10.604980945587158, '<=', 1.1936511918902397, '<=', 6.657510280609131, '<=', 8.957874298095703, '<=', 0.8254246115684509, '<=', 1.9773771166801453, '<=', 0.1877131164073944, '<=', 2.40395188331604, '<=', 0.008085265755653381, '<=', 2.4103026390075684, '<=', 3.0880775451660156, '<=', 6.214353799819946, '<=', 4.


5 [441, 355, 25, 207, 389, 92, 501, 407, 206, 11, 262, 209, 144, 163, 233, 442, 259, 484, 255, 474, 224, 375, 148, 303, 507, 440] ['<=', 10.604980945587158, '<=', 1.1936511918902397, '<=', 6.657510280609131, '<=', 8.957874298095703, '<=', 0.8254246115684509, '<=', 1.9773771166801453, '<=', 0.1877131164073944, '<=', 2.40395188331604, '<=', 0.008085265755653381, '<=', 2.4103026390075684, '<=', 3.0880775451660156, '<=', 6.214353799819946, '<=', 4.471221923828125, '<=', 7.043302059173584, '<=', 9.08201551437378, '<=', 1.5570796728134155, '<=', 3.654170513153076, '<=', 0.04623603820800781, '<=', 7.0666351318359375, '<=', 1.1264054775238037, '>', 0.5040231347084045, '<=', 7.760706424713135, '<=', 3.589111089706421, '<=', 5.3053460121154785, '>', 6.2375359535217285, '<=', 11.48403549194336] 8
5 [441, 355, 25, 207, 389, 92, 501, 407, 206, 11, 262, 335] ['<=', 10.604980945587158, '<=', 1.1936511918902397, '<=', 6.657510280609131, '<=', 8.957874298095703, '<=', 0.8254246115684509, '<=', 1.97737

100%|██████████| 1678/1678 [00:00<00:00, 435441.57it/s]


 CORRECT PATTERNS ACT 2:

3 [355, 441, 207, 0, 501, 407, 11, 389, 206, 8, 146, 408, 424, 233, 25, 294, 226, 262, 337, 327, 365, 410, 369, 181, 204, 347] ['<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5] 30
3 [355, 441, 207, 206, 288, 230, 262, 410, 212, 225, 204, 356, 175, 55] ['<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5] 21
3 [355, 441, 207, 0, 501, 407, 11, 389, 206, 8, 146, 408, 424, 233, 25, 294, 226, 262, 127, 484, 380, 24, 193, 39, 199, 333, 210] ['<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, 

4 [355, 441, 207, 206, 288, 230, 262, 410, 212, 225, 204, 356, 175] ['<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5] 1
4 [355, 441, 207, 206, 288, 230, 262, 410, 212, 225, 204, 353] ['<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5] 1
4 [355, 441, 207, 206, 288, 230, 262, 410, 291, 467, 101] ['<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5] 1
4 [355, 441, 207, 206, 288, 440, 410, 428, 157, 98, 68, 372, 174] ['<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5] 1
4 [355, 441, 207, 206, 288, 440, 489, 230, 216, 192, 197, 272, 468, 450, 432, 333, 327, 145, 262, 191, 186] ['<=', 0.5, '<=', 0.5, '>', 0.5, '<=', 0.5, '>', 0.5, '>', 0.5, '<=', 0.5, '<=', 0.5, '<=', 0.5, '<

In [ ]:
# INVOKE FOR EVERY CORRECT LABEL
def corr_match_pattern(layer_vals,suff,neuron_ids,neuron_sig):
   max_match_cnt = -1
   for ix in range(0,len(neuron_ids)):
     match_cnt = 0
     oper = -1
     for ind in range(0,len(neuron_ids[ix])):
       if (ind % 2 == 0):
         op = neuron_sig[ix][ind]
         if (op == '<='):
           oper = 0
         else:
           oper = 1
       else:
         v = neuron_ids[ix][ind]
         vsig = neuron_sig[ix][ind]
         val = layer_vals[v]
         # print(v,vsig,val,oper)
         if (oper == 0):
          if (val <= vsig):
            match_cnt = match_cnt + 1
         else:
          if (val > vsig):
            match_cnt = match_cnt + 1
         oper = -1

     if (match_cnt > max_match_cnt):
       max_match_cnt = match_cnt

   return max_match_cnt

def check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3, neuron_lay,neuron_ids,neuron_sig,support=[],supp_thres=-1):

   labs = []
   found = True;
   oper = -1
   layer_vals1 = (layer_vals1).flatten()
   layer_vals2 = (layer_vals2).flatten()
   layer_vals3 = (layer_vals3).flatten()


   for ix in range(0,len(neuron_ids)):
     if (len(support) > 0):
         if (support[ix] <= supp_thres):
           continue
     found = True
     for ind in range(0,len(neuron_ids[ix])):
       if (ind % 2 == 0):
         op = neuron_sig[ix][ind]
         if (op == '<='):
           oper = 0
         else:
           oper = 1
       else:
         v = neuron_ids[ix][ind]
         vsig = neuron_sig[ix][ind]
         val = 0
         if (neuron_lay[ix] == 1):
           val = layer_vals1[v]
         if (neuron_lay[ix] == 2):
           val = layer_vals2[v]
         if (neuron_lay[ix] == 3):
           val = layer_vals3[v]

         #print("oper:",oper,"layer:",neuron_lay[ix],"pattern value:", v, "pattern sig:",vsig, "inp value:",val)

         if (oper == 0):
          if (val > vsig):
            found = False
          #  print('False')
            break
         else:
          if (val <= vsig):
            found = False
           # print('False')
            break
         oper = -1
     if (found == True):
       #break
       labs.append(ix)

   return labs
   #if (found == False):
   #   return -1
   #else:
   #  return ix

def check_pattern_inter(layer_vals,suff,neuron_ids,neuron_sig,VAL = True,ALL=False):

   if (VAL == False):
      if ((suff[:,neuron_ids][0] == neuron_sig).all(axis=0)):
        return True
      else:
        return False


   found = True;
   oper = -1
   layer_vals = (layer_vals).flatten()

   for ix in range(0,len(neuron_ids)):
     found = True
     for ind in range(0,len(neuron_ids[ix])):
       if (ind % 2 == 0):
         op = neuron_sig[ix][ind]
         if (op == '<='):
           oper = 0
         else:
           oper = 1
       else:
         v = neuron_ids[ix][ind]
         vsig = neuron_sig[ix][ind]
         val = layer_vals[v]
         #print(oper, v, vsig, val)
         if (oper == 0):
          if (val > vsig):
            found = False
          #  print('False')
            break
         else:
          if (val <= vsig):
            found = False
           # print('False')
            break
         oper = -1
     if (found == True):
       break

   if (found == False):
      return -1
   else:
     return ix

In [ ]:
def check_pattern(layer_vals,suff,neuron_ids,neuron_sig,VAL = True,ALL=False):
   #layer = 'activation_3'  #layer name, get it from the model summary
   #neuron_ids =  [-1,71,-1,20,-1,1,-1,28,-1,79,-1,29,-1,39,-1,49,-1,42,-1,33,-1,114,-1,117,-1,88,-1,31,-1,36,-1,33,-1,17,-1,117,-1,1,-1,28,-1,97] # neuron ids in the pattern
   #neuron_sig =  ['>',0.435630053,'>',4.067234278,'<=',42.78802872,'<=',20.19964218,'<=',41.11421585,'<=',23.87646389,'<=',15.27161694,'<=',36.27468491,'<=',30.84732342,'<=',40.63782883,'<=',25.80421829,'<=',43.16035843,'<=',38.44324303,'<=',66.91875458,'<=',26.18983078,'<=',16.70914364,'<=',41.36343193,'<=',35.72474098,'<=',35.5690403,'<=',14.66370487,'<=',40.59473419189453]

   if (VAL == False):
      if ((suff[:,neuron_ids][0] == neuron_sig).all(axis=0)):
        return True
      else:
        return False

   found = True;
   #Integer v = null;
	#			Double vsig = null;
	#			String op = null;
	#			int oper = -1;
   oper = -1
   for ind in range(0,len(neuron_ids)):
     if (ind % 2 == 0):
       op = neuron_sig[ind]
       if (op == '<='):
         oper = 0
       else:
         oper = 1
     else:
       v = neuron_ids[ind]
       vsig = neuron_sig[ind]
       val = layer_vals[v]
      # print(v,vsig,val,oper)
       if (oper == 0):
         if (val > vsig):
           found = False
           break
       else:
         if (val <= vsig):
            found = False
            break
       oper = -1

   return found

In [ ]:
# #### STRATEGY 1A, CLEAN DATA
# strat1a_start_time = time.time()

# neuron_ids =[]
# inc_neuron_ids=[]
# neuron_sig = []

# Cneuron_ids =[]
# C_neuron_ids=[]
# Cneuron_sig = []
# Cneuron_cl = []
# Cneuron_lay = []

# corr_invs_sel_supp = []
# corr_invs_sel_neus = []
# corr_invs_sel_sig = []
# corr_invs_sel_labs = []
# corr_invs_sel_lay = []


# for ix in range (0, len(corr_invs_sel_supp1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   corr_invs_sel_supp.append(corr_invs_sel_supp1[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus1[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig1[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs1[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay1[ix])



# for ix in range (0, len(corr_invs_sel_supp2)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp2[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus2[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig2[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs2[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay2[ix])


# for ix in range (0, len(corr_invs_sel_supp)-1):
#     for iy in range(ix +1, len(corr_invs_sel_supp)):
#         if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
#           temp = corr_invs_sel_supp[iy]
#           corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
#           corr_invs_sel_supp[ix] = temp
#           temp = corr_invs_sel_neus[iy]
#           corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
#           corr_invs_sel_neus[ix] = temp
#           temp = corr_invs_sel_sig[iy]
#           corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
#           corr_invs_sel_sig[ix] = temp
#           temp = corr_invs_sel_labs[iy]
#           corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
#           corr_invs_sel_labs[ix] = temp
#           temp = corr_invs_sel_lay[iy]
#           corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
#           corr_invs_sel_lay[ix] = temp


# for indx in range (0, len(corr_invs_sel_neus)):
#       Cneu_ids = []
#       for indx1 in range (0, len(corr_invs_sel_neus[indx])):
#         Cneu_ids.append(-1)
#         Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
#       Cneuron_ids.append(Cneu_ids)
#       C_neuron_ids.append(corr_invs_sel_neus[indx])


# for indx in range (0, len(corr_invs_sel_sig)):
#       Cneuron_sig.append(corr_invs_sel_sig[indx])
#       Cneuron_cl.append(corr_invs_sel_labs[indx])
#       Cneuron_lay.append(corr_invs_sel_lay[indx])

# print("\n CORRECT PATTERNS\n")
# for indx in range (0, len(Cneuron_cl)):
#   print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])


# x = copy.deepcopy(val_X)
# cnt = 0
# correct = 0

# labels = (model.predict(x)).argmax(axis=1)
# ideals = val_Y




# true_positives = 0
# true_negatives = 0
# false_positives = 0
# false_negatives = 0
# cnt_not_fnd = 0
# broke = 0
# pois_pat = 0


# PASS = 0
# PASS_bef = 0
# FAIL = 0
# FAIL_bef = 0

# clean_pass = 0
# clean_fail = 0
# pois_pass = 0
# pois_fail = 0


# for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
#     cnt = cnt + 1
#     image = x[inp_cnt]
#     label = labels[inp_cnt]

#    # inp = image
#    # inc_layer = 'dense'  #layer name, get it from the model summary
#    # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

#     #layer_vals = inc_suff[0]
#     #suff = []



#     img = np.zeros((32,32,3),dtype=float)
#     for ix in range(0,32):
#       for iy in range(0,32):
#         for iz in range(0,3):
#           img[ix][iy][iz] = (float(image[ix][iy][iz]))

#     image_array = np.zeros((1,32,32,3),dtype=float)
#     image_array[0]=img
#     img_mod = np.expand_dims(img,axis=0)


#     inp = image
#     inc_layer = 'dense'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals1 = inc_suff[0]
#     suff = []

#     inp = image
#     inc_layer = 'activation_4'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals2 = inc_suff[0]


#     layer_vals3 = np.array([])



#     max_lab7 = False
#     match = -1
#     match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig)
#     print("MATCH:", match)
#     Same = True
#     if (len(match) == 0):
#       cnt_not_fnd = cnt_not_fnd + 1
#       new_lbl = labels[inp_cnt]
#     else:
#       if (Cneuron_lay[match[0]] == 3):
#         max_lab7 = True
#         if (len(match) > 1):
#           new_lbl = Cneuron_cl[match[1]]
#         else:
#           new_lbl = labels[inp_cnt]
#       else:
#         new_lbl = Cneuron_cl[match[0]]

#       Same = True
#       prev_lab = -1
#       for indx in range(0,len(match)):
#          print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
#          if (Cneuron_lay[match[indx]] ==3):
#            continue
#          if (prev_lab != -1 and Cneuron_cl[match[indx]] != prev_lab):
#              Same=False
#          prev_lab = Cneuron_cl[match[indx]]




#     if (new_lbl == ideals[inp_cnt]):
#       PASS = PASS + 1
#       if (labels[inp_cnt] != ideals[inp_cnt]):
#         correct = correct + 1
#         if (max_lab7 == True):
#           pois_pat = pois_pat + 1
#     else:
#       # if (Same == False):
#       #   print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
#       FAIL = FAIL + 1
#       if (labels[inp_cnt] == ideals[inp_cnt]):
#         broke = broke + 1

# print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

# print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
# print('CORRECTED:', float(correct/cnt)*100)
# print('BROKEN:', float(broke/cnt)*100)
# print('POIS PAT',pois_pat)
# print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )

# strat1a_time = (time.time() - strat1a_start_time)/ len(x)


Streaming output truncated to the last 5000 lines.
LAYER,LABEL,SUPP 2 0 19
MATCH: [420, 671]
LAYER,LABEL,SUPP 1 5 3
LAYER,LABEL,SUPP 2 0 2
MATCH: [15]
LAYER,LABEL,SUPP 1 2 73
MATCH: [105, 238]
LAYER,LABEL,SUPP 1 7 13
LAYER,LABEL,SUPP 2 5 5
MATCH: [999]
LAYER,LABEL,SUPP 2 5 1
MATCH: [5, 423]
LAYER,LABEL,SUPP 2 6 194
LAYER,LABEL,SUPP 1 5 3
MATCH: [94, 183]
LAYER,LABEL,SUPP 2 4 14
LAYER,LABEL,SUPP 1 3 7
MATCH: [6, 468]
LAYER,LABEL,SUPP 1 0 171
LAYER,LABEL,SUPP 2 8 3
MATCH: [217, 1270]
LAYER,LABEL,SUPP 2 3 6
LAYER,LABEL,SUPP 1 3 1
MATCH: [4, 37]
LAYER,LABEL,SUPP 1 1 196
LAYER,LABEL,SUPP 2 1 35
MATCH: [228]
LAYER,LABEL,SUPP 1 5 6
MATCH: [8, 1222]
LAYER,LABEL,SUPP 2 1 120
LAYER,LABEL,SUPP 1 3 1
MATCH: [78]
LAYER,LABEL,SUPP 1 5 17
MATCH: [332]
LAYER,LABEL,SUPP 1 8 4
MATCH: [332, 361]
LAYER,LABEL,SUPP 1 8 4
LAYER,LABEL,SUPP 2 8 4
MATCH: [4, 16]
LAYER,LABEL,SUPP 1 1 196
LAYER,LABEL,SUPP 2 1 73
MATCH: [92]
LAYER,LABEL,SUPP 1 0 15
MATCH: [19]
LAYER,LABEL,SUPP 2 2 65
MATCH: [0, 1]
LAYER,LABEL,SUPP

In [ ]:
# #### STRATEGY 1b, CLEAN DATA
# strat1b_start_time = time.time()

# neuron_ids =[]
# inc_neuron_ids=[]
# neuron_sig = []

# Cneuron_ids =[]
# C_neuron_ids=[]
# Cneuron_sig = []
# Cneuron_cl = []
# Cneuron_lay = []

# corr_invs_sel_supp = []
# corr_invs_sel_neus = []
# corr_invs_sel_sig = []
# corr_invs_sel_labs = []
# corr_invs_sel_lay = []


# MCneuron_ids =[]
# MC_neuron_ids=[]
# MCneuron_sig = []
# MCneuron_cl = []
# MCneuron_lay = []

# Minvs_sel_supp = []
# Minvs_sel_neus = []
# Minvs_sel_sig = []
# Minvs_sel_labs = []
# Minvs_sel_lay = []

# for ix in range (0, len(corr_invs_sel_supp1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   corr_invs_sel_supp.append(corr_invs_sel_supp1[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus1[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig1[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs1[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay1[ix])



# for ix in range (0, len(corr_invs_sel_supp2)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp2[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus2[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig2[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs2[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay2[ix])


# for ix in range (0, len(PMinvs_sel_sup1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   Minvs_sel_supp.append(PMinvs_sel_sup1[ix])
#   Minvs_sel_neus.append(PMinvs_sel_neus1[ix])
#   Minvs_sel_sig.append(PMinvs_sel_sig1[ix])
#   Minvs_sel_labs.append(PMinvs_sel_cl1[ix])
#   Minvs_sel_lay.append(PMinvs_sel_lay1[ix])



# for ix in range (0, len(PMinvs_sel_sup2)):
#   Minvs_sel_supp.append(PMinvs_sel_sup2[ix])
#   Minvs_sel_neus.append(PMinvs_sel_neus2[ix])
#   Minvs_sel_sig.append(PMinvs_sel_sig2[ix])
#   Minvs_sel_labs.append(PMinvs_sel_cl2[ix])
#   Minvs_sel_lay.append(PMinvs_sel_lay2[ix])




# for ix in range (0, len(corr_invs_sel_supp)-1):
#     for iy in range(ix +1, len(corr_invs_sel_supp)):
#         if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
#           temp = corr_invs_sel_supp[iy]
#           corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
#           corr_invs_sel_supp[ix] = temp
#           temp = corr_invs_sel_neus[iy]
#           corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
#           corr_invs_sel_neus[ix] = temp
#           temp = corr_invs_sel_sig[iy]
#           corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
#           corr_invs_sel_sig[ix] = temp
#           temp = corr_invs_sel_labs[iy]
#           corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
#           corr_invs_sel_labs[ix] = temp
#           temp = corr_invs_sel_lay[iy]
#           corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
#           corr_invs_sel_lay[ix] = temp


# for indx in range (0, len(corr_invs_sel_neus)):
#       Cneu_ids = []
#       for indx1 in range (0, len(corr_invs_sel_neus[indx])):
#         Cneu_ids.append(-1)
#         Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
#       Cneuron_ids.append(Cneu_ids)
#       C_neuron_ids.append(corr_invs_sel_neus[indx])


# for indx in range (0, len(corr_invs_sel_sig)):
#       Cneuron_sig.append(corr_invs_sel_sig[indx])
#       Cneuron_cl.append(corr_invs_sel_labs[indx])
#       Cneuron_lay.append(corr_invs_sel_lay[indx])

# print("\n CORRECT PATTERNS\n")
# for indx in range (0, len(Cneuron_cl)):
#   print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])


# for ix in range (0, len(Minvs_sel_supp)-1):
#     for iy in range(ix +1, len(Minvs_sel_supp)):
#         if (Minvs_sel_supp[iy] > Minvs_sel_supp[ix]):
#           temp = Minvs_sel_supp[iy]
#           Minvs_sel_supp[iy] = Minvs_sel_supp[ix]
#           Minvs_sel_supp[ix] = temp
#           temp = Minvs_sel_neus[iy]
#           Minvs_sel_neus[iy] = Minvs_sel_neus[ix]
#           Minvs_sel_neus[ix] = temp
#           temp = Minvs_sel_sig[iy]
#           Minvs_sel_sig[iy] = Minvs_sel_sig[ix]
#           Minvs_sel_sig[ix] = temp
#           temp = Minvs_sel_labs[iy]
#           Minvs_sel_labs[iy] = Minvs_sel_labs[ix]
#           Minvs_sel_labs[ix] = temp
#           temp = Minvs_sel_lay[iy]
#           Minvs_sel_lay[iy] = Minvs_sel_lay[ix]
#           Minvs_sel_lay[ix] = temp


# for indx in range (0, len(Minvs_sel_neus)):
#       MCneu_ids = []
#       for indx1 in range (0, len(Minvs_sel_neus[indx])):
#         MCneu_ids.append(-1)
#         MCneu_ids.append(Minvs_sel_neus[indx][indx1])
#       MCneuron_ids.append(MCneu_ids)
#       MC_neuron_ids.append(Minvs_sel_neus[indx])


# for indx in range (0, len(Minvs_sel_sig)):
#       MCneuron_sig.append(Minvs_sel_sig[indx])
#       MCneuron_cl.append(Minvs_sel_labs[indx])
#       MCneuron_lay.append(Minvs_sel_lay[indx])

# print("\n MIS-CLASSIFICATION PATTERNS\n")
# for indx in range (0, len(MCneuron_cl)):
#   print(MCneuron_cl[indx],Minvs_sel_supp[indx],MCneuron_lay[indx],MC_neuron_ids[indx],MCneuron_sig[indx])

# x = copy.deepcopy(val_X)
# cnt = 0
# correct = 0

# labels = (model.predict(x)).argmax(axis=1)
# ideals = val_Y




# true_positives = 0
# true_negatives = 0
# false_positives = 0
# false_negatives = 0
# cnt_not_fnd = 0
# broke = 0
# pois_pat = 0


# PASS = 0
# PASS_bef = 0
# FAIL = 0
# FAIL_bef = 0

# clean_pass = 0
# clean_fail = 0
# pois_pass = 0
# pois_fail = 0


# for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
#     cnt = cnt + 1
#     image = x[inp_cnt]
#     label = labels[inp_cnt]

#    # inp = image
#    # inc_layer = 'dense'  #layer name, get it from the model summary
#    # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

#     #layer_vals = inc_suff[0]
#     #suff = []



#     img = np.zeros((32,32,3),dtype=float)
#     for ix in range(0,32):
#       for iy in range(0,32):
#         for iz in range(0,3):
#           img[ix][iy][iz] = (float(image[ix][iy][iz]))

#     image_array = np.zeros((1,32,32,3),dtype=float)
#     image_array[0]=img
#     img_mod = np.expand_dims(img,axis=0)


#     inp = image
#     inc_layer = 'dense'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals1 = inc_suff[0]
#     suff = []

#     inp = image
#     inc_layer = 'activation_4'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals2 = inc_suff[0]


#     layer_vals3 = np.array([])



#     max_lab7 = False
#     match1 = -1
#     Same = True
#     match1 = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,MCneuron_lay,MCneuron_ids,MCneuron_sig)
#     print("MATCH MIS-CLASS:", match1)
#     if (len(match1) == 0):
#       cnt_not_fnd = cnt_not_fnd + 1
#       new_lbl = labels[inp_cnt]
#     else:
#       match = -1
#       match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig)
#       if (len(match) == 0):
#        # cnt_not_fnd = cnt_not_fnd + 1
#         new_lbl = labels[inp_cnt]
#       else:
#         if (Cneuron_lay[match[0]] == 3):
#           if (len(match) > 1):
#             new_lbl = Cneuron_cl[match[1]]
#           else:
#             new_lbl = labels[inp_cnt]
#         else:
#           new_lbl = Cneuron_cl[match[0]]

#         Same = True
#         prev_lab = -1
#         for indx in range(0,len(match)):
#           print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
#           if (Cneuron_lay[match[indx]] ==3):
#             continue
#           if (prev_lab != -1 and Cneuron_cl[match[indx]] != prev_lab):
#             Same=False
#           prev_lab = Cneuron_cl[match[indx]]




#     if (new_lbl == ideals[inp_cnt]):
#       PASS = PASS + 1
#       if (labels[inp_cnt] != ideals[inp_cnt]):
#         correct = correct + 1
#         if (max_lab7 == True):
#           pois_pat = pois_pat + 1
#     else:
#       if (Same == False):
#         print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
#       FAIL = FAIL + 1
#       if (labels[inp_cnt] == ideals[inp_cnt]):
#         broke = broke + 1

# print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

# print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
# print('CORRECTED:', float(correct/cnt)*100)
# print('BROKEN:', float(broke/cnt)*100)
# print('POIS PAT',pois_pat)
# print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )

# strat1b_time = (time.time() - strat1b_start_time)/ len(x)




In [ ]:
#### STRATEGY 1C, CLEAN DATA
strat1c_start_time = time.time()

neuron_ids =[]
inc_neuron_ids=[]
neuron_sig = []

Cneuron_ids =[]
C_neuron_ids=[]
Cneuron_sig = []
Cneuron_cl = []
Cneuron_lay = []

corr_invs_sel_supp = []
corr_invs_sel_neus = []
corr_invs_sel_sig = []
corr_invs_sel_labs = []
corr_invs_sel_lay = []


MCneuron_ids =[]
MC_neuron_ids=[]
MCneuron_sig = []
MCneuron_cl = []
MCneuron_lay = []

Minvs_sel_supp = []
Minvs_sel_neus = []
Minvs_sel_sig = []
Minvs_sel_labs = []
Minvs_sel_lay = []

for ix in range (0, len(Rcorr_invs_sel_supp1)):
  #if (corr_invs_sel_supp1[ix] <= 20):
  #   continue
  corr_invs_sel_supp.append(Rcorr_invs_sel_supp1[ix])
  corr_invs_sel_neus.append(Rcorr_invs_sel_neus1[ix])
  corr_invs_sel_sig.append(Rcorr_invs_sel_sig1[ix])
  corr_invs_sel_labs.append(Rcorr_invs_sel_labs1[ix])
  corr_invs_sel_lay.append(Rcorr_invs_sel_lay1[ix])



for ix in range (0, len(Rcorr_invs_sel_supp2)):
  corr_invs_sel_supp.append(Rcorr_invs_sel_supp2[ix])
  corr_invs_sel_neus.append(Rcorr_invs_sel_neus2[ix])
  corr_invs_sel_sig.append(Rcorr_invs_sel_sig2[ix])
  corr_invs_sel_labs.append(Rcorr_invs_sel_labs2[ix])
  corr_invs_sel_lay.append(Rcorr_invs_sel_lay2[ix])


for ix in range (0, len(PMinvs_sel_sup1)):
  #if (corr_invs_sel_supp1[ix] <= 20):
  #   continue
  Minvs_sel_supp.append(PMinvs_sel_sup1[ix])
  Minvs_sel_neus.append(PMinvs_sel_neus1[ix])
  Minvs_sel_sig.append(PMinvs_sel_sig1[ix])
  Minvs_sel_labs.append(PMinvs_sel_cl1[ix])
  Minvs_sel_lay.append(PMinvs_sel_lay1[ix])



for ix in range (0, len(PMinvs_sel_sup2)):
  Minvs_sel_supp.append(PMinvs_sel_sup2[ix])
  Minvs_sel_neus.append(PMinvs_sel_neus2[ix])
  Minvs_sel_sig.append(PMinvs_sel_sig2[ix])
  Minvs_sel_labs.append(PMinvs_sel_cl2[ix])
  Minvs_sel_lay.append(PMinvs_sel_lay2[ix])




for ix in range (0, len(corr_invs_sel_supp)-1):
    for iy in range(ix +1, len(corr_invs_sel_supp)):
        if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
          temp = corr_invs_sel_supp[iy]
          corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
          corr_invs_sel_supp[ix] = temp
          temp = corr_invs_sel_neus[iy]
          corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
          corr_invs_sel_neus[ix] = temp
          temp = corr_invs_sel_sig[iy]
          corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
          corr_invs_sel_sig[ix] = temp
          temp = corr_invs_sel_labs[iy]
          corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
          corr_invs_sel_labs[ix] = temp
          temp = corr_invs_sel_lay[iy]
          corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
          corr_invs_sel_lay[ix] = temp


for indx in range (0, len(corr_invs_sel_neus)):
      Cneu_ids = []
      for indx1 in range (0, len(corr_invs_sel_neus[indx])):
        Cneu_ids.append(-1)
        Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
      Cneuron_ids.append(Cneu_ids)
      C_neuron_ids.append(corr_invs_sel_neus[indx])


for indx in range (0, len(corr_invs_sel_sig)):
      Cneuron_sig.append(corr_invs_sel_sig[indx])
      Cneuron_cl.append(corr_invs_sel_labs[indx])
      Cneuron_lay.append(corr_invs_sel_lay[indx])

print("\n CORRECT PATTERNS\n")
for indx in range (0, len(Cneuron_cl)):
  print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])


for ix in range (0, len(Minvs_sel_supp)-1):
    for iy in range(ix +1, len(Minvs_sel_supp)):
        if (Minvs_sel_supp[iy] > Minvs_sel_supp[ix]):
          temp = Minvs_sel_supp[iy]
          Minvs_sel_supp[iy] = Minvs_sel_supp[ix]
          Minvs_sel_supp[ix] = temp
          temp = Minvs_sel_neus[iy]
          Minvs_sel_neus[iy] = Minvs_sel_neus[ix]
          Minvs_sel_neus[ix] = temp
          temp = Minvs_sel_sig[iy]
          Minvs_sel_sig[iy] = Minvs_sel_sig[ix]
          Minvs_sel_sig[ix] = temp
          temp = Minvs_sel_labs[iy]
          Minvs_sel_labs[iy] = Minvs_sel_labs[ix]
          Minvs_sel_labs[ix] = temp
          temp = Minvs_sel_lay[iy]
          Minvs_sel_lay[iy] = Minvs_sel_lay[ix]
          Minvs_sel_lay[ix] = temp


for indx in range (0, len(Minvs_sel_neus)):
      MCneu_ids = []
      for indx1 in range (0, len(Minvs_sel_neus[indx])):
        MCneu_ids.append(-1)
        MCneu_ids.append(Minvs_sel_neus[indx][indx1])
      MCneuron_ids.append(MCneu_ids)
      MC_neuron_ids.append(Minvs_sel_neus[indx])


for indx in range (0, len(Minvs_sel_sig)):
      MCneuron_sig.append(Minvs_sel_sig[indx])
      MCneuron_cl.append(Minvs_sel_labs[indx])
      MCneuron_lay.append(Minvs_sel_lay[indx])

print("\n MIS-CLASSIFICATION PATTERNS\n")
for indx in range (0, len(MCneuron_cl)):
  print(MCneuron_cl[indx],Minvs_sel_supp[indx],MCneuron_lay[indx],MC_neuron_ids[indx],MCneuron_sig[indx])

x = copy.deepcopy(val_X)
cnt = 0
correct = 0

labels = (model.predict(x)).argmax(axis=1)
ideals = val_Y




true_positives = 0
true_negatives = 0
false_positives = 0
false_negatives = 0
cnt_not_fnd = 0
broke = 0
pois_pat = 0


PASS = 0
PASS_bef = 0
FAIL = 0
FAIL_bef = 0

clean_pass = 0
clean_fail = 0
pois_pass = 0
pois_fail = 0


for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
    cnt = cnt + 1
    image = x[inp_cnt]
    label = labels[inp_cnt]

   # inp = image
   # inc_layer = 'dense'  #layer name, get it from the model summary
   # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

    #layer_vals = inc_suff[0]
    #suff = []



    img = np.zeros((32,32,3),dtype=float)
    for ix in range(0,32):
      for iy in range(0,32):
        for iz in range(0,3):
          img[ix][iy][iz] = (float(image[ix][iy][iz]))

    image_array = np.zeros((1,32,32,3),dtype=float)
    image_array[0]=img
    img_mod = np.expand_dims(img,axis=0)


    inp = image
    inc_layer = 'dense'  #layer name, get it from the model summary
    inc_suff = fingerprint_suffix_vals(inp, inc_layer)
    layer_vals1 = inc_suff[0]
    suff = []

    inp = image
    inc_layer = 'activation_4'  #layer name, get it from the model summary
    inc_suff = fingerprint_suffix_vals(inp, inc_layer)
    layer_vals2 = inc_suff[0]


    layer_vals3 = np.array([])



    max_lab7 = False
    match1 = -1

    Same = True
    match1 = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,MCneuron_lay,MCneuron_ids,MCneuron_sig)
    print("MATCH MIS-CLASS:", match1)
    if (len(match1) == 0):
      cnt_not_fnd = cnt_not_fnd + 1
      new_lbl = labels[inp_cnt]
    else:
      match = -1
      match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig)
      if (len(match) == 0):
      #  cnt_not_fnd = cnt_not_fnd + 1
        new_lbl = labels[inp_cnt]
      else:
        if (Cneuron_lay[match[0]] == 3):
          if (len(match) > 1):
            new_lbl = Cneuron_cl[match[1]]
          else:
            new_lbl = labels[inp_cnt]
        else:
          new_lbl = Cneuron_cl[match[0]]

        Same = True
        prev_lab = -1
        for indx in range(0,len(match)):
          print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
          if (Cneuron_lay[match[indx]] ==3):
            continue
          if (prev_lab != -1 and Cneuron_cl[match[indx]] != prev_lab):
            Same=False
          prev_lab = Cneuron_cl[match[indx]]




    if (new_lbl == ideals[inp_cnt]):
      PASS = PASS + 1
      if (labels[inp_cnt] != ideals[inp_cnt]):
        correct = correct + 1
        if (max_lab7 == True):
          pois_pat = pois_pat + 1
    else:
      if (Same == False):
        print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
      FAIL = FAIL + 1
      if (labels[inp_cnt] == ideals[inp_cnt]):
        broke = broke + 1

print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
print('CORRECTED:', float(correct/cnt)*100)
print('BROKEN:', float(broke/cnt)*100)
print('POIS PAT',pois_pat)
print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )

strat1c_time = (time.time() - strat1c_start_time)/ len(x)



Streaming output truncated to the last 5000 lines.
MATCH MIS-CLASS: []
MATCH MIS-CLASS: [76]
LAYER,LABEL,SUPP 2 8 21
LAYER,LABEL,SUPP 1 0 8
OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL: 9 9 [63, 169] 8
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MATCH MIS-CLASS: []
MAT

In [ ]:
# #### STRATEGY 1A, POIS DATA
# strat1a_start_pois_time = time.time()

# neuron_ids =[]
# inc_neuron_ids=[]
# neuron_sig = []

# Cneuron_ids =[]
# C_neuron_ids=[]
# Cneuron_sig = []
# Cneuron_cl = []
# Cneuron_lay = []

# corr_invs_sel_supp = []
# corr_invs_sel_neus = []
# corr_invs_sel_sig = []
# corr_invs_sel_labs = []
# corr_invs_sel_lay = []

# for ix in range (0, len(corr_invs_sel_supp1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   corr_invs_sel_supp.append(corr_invs_sel_supp1[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus1[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig1[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs1[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay1[ix])

# # for ix in range (0, len(corr_invs_sel_supp1a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp1a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus1a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig1a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs1a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay1a[ix])

# for ix in range (0, len(corr_invs_sel_supp2)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp2[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus2[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig2[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs2[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay2[ix])

# # for ix in range (0, len(corr_invs_sel_supp2a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp2a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus2a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig2a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs2a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay2a[ix])




# for ix in range (0, len(corr_invs_sel_supp)-1):
#     for iy in range(ix +1, len(corr_invs_sel_supp)):
#         if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
#           temp = corr_invs_sel_supp[iy]
#           corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
#           corr_invs_sel_supp[ix] = temp
#           temp = corr_invs_sel_neus[iy]
#           corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
#           corr_invs_sel_neus[ix] = temp
#           temp = corr_invs_sel_sig[iy]
#           corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
#           corr_invs_sel_sig[ix] = temp
#           temp = corr_invs_sel_labs[iy]
#           corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
#           corr_invs_sel_labs[ix] = temp
#           temp = corr_invs_sel_lay[iy]
#           corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
#           corr_invs_sel_lay[ix] = temp


# for indx in range (0, len(corr_invs_sel_neus)):
#       Cneu_ids = []
#       for indx1 in range (0, len(corr_invs_sel_neus[indx])):
#         Cneu_ids.append(-1)
#         Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
#       Cneuron_ids.append(Cneu_ids)
#       C_neuron_ids.append(corr_invs_sel_neus[indx])


# for indx in range (0, len(corr_invs_sel_sig)):
#       Cneuron_sig.append(corr_invs_sel_sig[indx])
#       Cneuron_cl.append(corr_invs_sel_labs[indx])
#       Cneuron_lay.append(corr_invs_sel_lay[indx])

# print("\n CORRECT PATTERNS\n")
# for indx in range (0, len(Cneuron_cl)):
#   print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])


# x = copy.deepcopy(Pval_X)
# cnt = 0
# correct = 0

# labels = (model.predict(x)).argmax(axis=1)
# ideals = Pval_Y




# true_positives = 0
# true_negatives = 0
# false_positives = 0
# false_negatives = 0
# cnt_not_fnd = 0
# broke = 0
# pois_pat = 0


# PASS = 0
# PASS_bef = 0
# FAIL = 0
# FAIL_bef = 0

# clean_pass = 0
# clean_fail = 0
# pois_pass = 0
# pois_fail = 0


# for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
#     cnt = cnt + 1
#     image = x[inp_cnt]
#     label = labels[inp_cnt]

#    # inp = image
#    # inc_layer = 'dense'  #layer name, get it from the model summary
#    # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

#     #layer_vals = inc_suff[0]
#     #suff = []


#     img = np.zeros((32,32,3),dtype=float)
#     for ix in range(0,32):
#       for iy in range(0,32):
#         for iz in range(0,3):
#           img[ix][iy][iz] = (float(image[ix][iy][iz]))

#     image_array = np.zeros((1,32,32,3),dtype=float)
#     image_array[0]=img
#     img_mod = np.expand_dims(img,axis=0)


#     inp = image
#     inc_layer = 'dense'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals1 = inc_suff[0]
#     suff = []

#     inp = image
#     inc_layer = 'activation_4'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals2 = inc_suff[0]


#     layer_vals3 = np.array([])



#     max_lab7 = False
#     match = -1
#     Same = True
#     match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig)
#     print("MATCH:", match)
#     if (len(match) == 0):
#       cnt_not_fnd = cnt_not_fnd + 1
#       new_lbl = labels[inp_cnt]
#     else:
#       if (Cneuron_lay[match[0]] == 3):
#         max_lab7 = True
#         if (len(match) > 1):
#           new_lbl = Cneuron_cl[match[1]]
#         else:
#           new_lbl = labels[inp_cnt]
#       else:
#         new_lbl = Cneuron_cl[match[0]]

#       Same = True
#       prev_lab = -1
#       for indx in range(0,len(match)):
#          print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
#          if (Cneuron_lay[match[indx]] ==3):
#            continue
#          if (prev_lab != -1 and Cneuron_cl[match[indx]] != prev_lab):
#              Same=False
#          prev_lab = Cneuron_cl[match[indx]]




#     if (new_lbl == ideals[inp_cnt]):
#       PASS = PASS + 1
#       if (labels[inp_cnt] != ideals[inp_cnt]):
#         correct = correct + 1
#         if (max_lab7 == True):
#           pois_pat = pois_pat + 1
#     else:
#       if (Same == False):
#         print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
#       FAIL = FAIL + 1
#       if (labels[inp_cnt] == ideals[inp_cnt]):
#         broke = broke + 1

# print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

# print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
# print('CORRECTED:', float(correct/cnt)*100)
# print('BROKEN:', float(broke/cnt)*100)
# print('POIS PAT',pois_pat)
# print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )

# strat1a_pois_time = (time.time() - strat1a_start_pois_time)/ len(x)

# print("STRAT 1A RUNTIME:", (strat1a_pois_time + strat1a_time)/2.0)


In [ ]:
# #### STRATEGY 1B, POIS DATA
# strat1b_start_pois_time = time.time()

# neuron_ids =[]
# inc_neuron_ids=[]
# neuron_sig = []

# Cneuron_ids =[]
# C_neuron_ids=[]
# Cneuron_sig = []
# Cneuron_cl = []
# Cneuron_lay = []

# corr_invs_sel_supp = []
# corr_invs_sel_neus = []
# corr_invs_sel_sig = []
# corr_invs_sel_labs = []
# corr_invs_sel_lay = []


# MCneuron_ids =[]
# MC_neuron_ids=[]
# MCneuron_sig = []
# MCneuron_cl = []
# MCneuron_lay = []

# Minvs_sel_supp = []
# Minvs_sel_neus = []
# Minvs_sel_sig = []
# Minvs_sel_labs = []
# Minvs_sel_lay = []

# for ix in range (0, len(corr_invs_sel_supp1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   corr_invs_sel_supp.append(corr_invs_sel_supp1[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus1[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig1[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs1[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay1[ix])



# for ix in range (0, len(corr_invs_sel_supp2)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp2[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus2[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig2[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs2[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay2[ix])


# for ix in range (0, len(PMinvs_sel_sup1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   Minvs_sel_supp.append(PMinvs_sel_sup1[ix])
#   Minvs_sel_neus.append(PMinvs_sel_neus1[ix])
#   Minvs_sel_sig.append(PMinvs_sel_sig1[ix])
#   Minvs_sel_labs.append(PMinvs_sel_cl1[ix])
#   Minvs_sel_lay.append(PMinvs_sel_lay1[ix])



# for ix in range (0, len(PMinvs_sel_sup2)):
#   Minvs_sel_supp.append(PMinvs_sel_sup2[ix])
#   Minvs_sel_neus.append(PMinvs_sel_neus2[ix])
#   Minvs_sel_sig.append(PMinvs_sel_sig2[ix])
#   Minvs_sel_labs.append(PMinvs_sel_cl2[ix])
#   Minvs_sel_lay.append(PMinvs_sel_lay2[ix])




# for ix in range (0, len(corr_invs_sel_supp)-1):
#     for iy in range(ix +1, len(corr_invs_sel_supp)):
#         if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
#           temp = corr_invs_sel_supp[iy]
#           corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
#           corr_invs_sel_supp[ix] = temp
#           temp = corr_invs_sel_neus[iy]
#           corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
#           corr_invs_sel_neus[ix] = temp
#           temp = corr_invs_sel_sig[iy]
#           corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
#           corr_invs_sel_sig[ix] = temp
#           temp = corr_invs_sel_labs[iy]
#           corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
#           corr_invs_sel_labs[ix] = temp
#           temp = corr_invs_sel_lay[iy]
#           corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
#           corr_invs_sel_lay[ix] = temp


# for indx in range (0, len(corr_invs_sel_neus)):
#       Cneu_ids = []
#       for indx1 in range (0, len(corr_invs_sel_neus[indx])):
#         Cneu_ids.append(-1)
#         Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
#       Cneuron_ids.append(Cneu_ids)
#       C_neuron_ids.append(corr_invs_sel_neus[indx])


# for indx in range (0, len(corr_invs_sel_sig)):
#       Cneuron_sig.append(corr_invs_sel_sig[indx])
#       Cneuron_cl.append(corr_invs_sel_labs[indx])
#       Cneuron_lay.append(corr_invs_sel_lay[indx])

# print("\n CORRECT PATTERNS\n")
# for indx in range (0, len(Cneuron_cl)):
#   print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])


# for ix in range (0, len(Minvs_sel_supp)-1):
#     for iy in range(ix +1, len(Minvs_sel_supp)):
#         if (Minvs_sel_supp[iy] > Minvs_sel_supp[ix]):
#           temp = Minvs_sel_supp[iy]
#           Minvs_sel_supp[iy] = Minvs_sel_supp[ix]
#           Minvs_sel_supp[ix] = temp
#           temp = Minvs_sel_neus[iy]
#           Minvs_sel_neus[iy] = Minvs_sel_neus[ix]
#           Minvs_sel_neus[ix] = temp
#           temp = Minvs_sel_sig[iy]
#           Minvs_sel_sig[iy] = Minvs_sel_sig[ix]
#           Minvs_sel_sig[ix] = temp
#           temp = Minvs_sel_labs[iy]
#           Minvs_sel_labs[iy] = Minvs_sel_labs[ix]
#           Minvs_sel_labs[ix] = temp
#           temp = Minvs_sel_lay[iy]
#           Minvs_sel_lay[iy] = Minvs_sel_lay[ix]
#           Minvs_sel_lay[ix] = temp


# for indx in range (0, len(Minvs_sel_neus)):
#       MCneu_ids = []
#       for indx1 in range (0, len(Minvs_sel_neus[indx])):
#         MCneu_ids.append(-1)
#         MCneu_ids.append(Minvs_sel_neus[indx][indx1])
#       MCneuron_ids.append(MCneu_ids)
#       MC_neuron_ids.append(Minvs_sel_neus[indx])


# for indx in range (0, len(Minvs_sel_sig)):
#       MCneuron_sig.append(Minvs_sel_sig[indx])
#       MCneuron_cl.append(Minvs_sel_labs[indx])
#       MCneuron_lay.append(Minvs_sel_lay[indx])

# print("\n MIS-CLASSIFICATION PATTERNS\n")
# for indx in range (0, len(MCneuron_cl)):
#   print(MCneuron_cl[indx],Minvs_sel_supp[indx],MCneuron_lay[indx],MC_neuron_ids[indx],MCneuron_sig[indx])

# x = copy.deepcopy(Pval_X)
# cnt = 0
# correct = 0

# labels = (model.predict(x)).argmax(axis=1)
# ideals = Pval_Y




# true_positives = 0
# true_negatives = 0
# false_positives = 0
# false_negatives = 0
# cnt_not_fnd = 0
# broke = 0
# pois_pat = 0


# PASS = 0
# PASS_bef = 0
# FAIL = 0
# FAIL_bef = 0

# clean_pass = 0
# clean_fail = 0
# pois_pass = 0
# pois_fail = 0


# for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
#     cnt = cnt + 1
#     image = x[inp_cnt]
#     label = labels[inp_cnt]

#    # inp = image
#    # inc_layer = 'dense'  #layer name, get it from the model summary
#    # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

#     #layer_vals = inc_suff[0]
#     #suff = []



#     img = np.zeros((32,32,3),dtype=float)
#     for ix in range(0,32):
#       for iy in range(0,32):
#         for iz in range(0,3):
#           img[ix][iy][iz] = (float(image[ix][iy][iz]))

#     image_array = np.zeros((1,32,32,3),dtype=float)
#     image_array[0]=img
#     img_mod = np.expand_dims(img,axis=0)


#     inp = image
#     inc_layer = 'dense'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals1 = inc_suff[0]
#     suff = []

#     inp = image
#     inc_layer = 'activation_4'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals2 = inc_suff[0]


#     layer_vals3 = np.array([])



#     max_lab7 = False
#     match1 = -1
#     Same = True
#     match1 = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,MCneuron_lay,MCneuron_ids,MCneuron_sig)
#     print("MATCH MIS-CLASS:", match1)
#     if (len(match1) == 0):
#       cnt_not_fnd = cnt_not_fnd + 1
#       new_lbl = labels[inp_cnt]
#     else:
#       match = -1
#       match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig)
#       if (len(match) == 0):
#       #  cnt_not_fnd = cnt_not_fnd + 1
#         new_lbl = labels[inp_cnt]
#       else:
#         if (Cneuron_lay[match[0]] == 3):
#           if (len(match) > 1):
#             new_lbl = Cneuron_cl[match[1]]
#           else:
#             new_lbl = labels[inp_cnt]
#         else:
#           new_lbl = Cneuron_cl[match[0]]

#         Same = True
#         prev_lab = -1
#         for indx in range(0,len(match)):
#           print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
#           if (Cneuron_lay[match[indx]] ==3):
#             continue
#           if (prev_lab != -1 and Cneuron_cl[match[indx]] != prev_lab):
#             Same=False
#           prev_lab = Cneuron_cl[match[indx]]




#     if (new_lbl == ideals[inp_cnt]):
#       PASS = PASS + 1
#       if (labels[inp_cnt] != ideals[inp_cnt]):
#         correct = correct + 1
#         if (max_lab7 == True):
#           pois_pat = pois_pat + 1
#     else:
#       if (Same == False):
#         print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
#       FAIL = FAIL + 1
#       if (labels[inp_cnt] == ideals[inp_cnt]):
#         broke = broke + 1

# print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

# print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
# print('CORRECTED:', float(correct/cnt)*100)
# print('BROKEN:', float(broke/cnt)*100)
# print('POIS PAT',pois_pat)
# print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )

# strat1b_pois_time = (time.time() - strat1b_start_pois_time)/ len(x)

# print("STRAT 1B RUNTIME:", (strat1b_pois_time + strat1b_time)/2.0)



In [ ]:
#### STRATEGY 1C, POIS DATA
strat1c_start_pois_time = time.time()

neuron_ids =[]
inc_neuron_ids=[]
neuron_sig = []

Cneuron_ids =[]
C_neuron_ids=[]
Cneuron_sig = []
Cneuron_cl = []
Cneuron_lay = []

corr_invs_sel_supp = []
corr_invs_sel_neus = []
corr_invs_sel_sig = []
corr_invs_sel_labs = []
corr_invs_sel_lay = []


MCneuron_ids =[]
MC_neuron_ids=[]
MCneuron_sig = []
MCneuron_cl = []
MCneuron_lay = []

Minvs_sel_supp = []
Minvs_sel_neus = []
Minvs_sel_sig = []
Minvs_sel_labs = []
Minvs_sel_lay = []

for ix in range (0, len(Rcorr_invs_sel_supp1)):
  #if (corr_invs_sel_supp1[ix] <= 20):
  #   continue
  corr_invs_sel_supp.append(Rcorr_invs_sel_supp1[ix])
  corr_invs_sel_neus.append(Rcorr_invs_sel_neus1[ix])
  corr_invs_sel_sig.append(Rcorr_invs_sel_sig1[ix])
  corr_invs_sel_labs.append(Rcorr_invs_sel_labs1[ix])
  corr_invs_sel_lay.append(Rcorr_invs_sel_lay1[ix])



for ix in range (0, len(Rcorr_invs_sel_supp2)):
  corr_invs_sel_supp.append(Rcorr_invs_sel_supp2[ix])
  corr_invs_sel_neus.append(Rcorr_invs_sel_neus2[ix])
  corr_invs_sel_sig.append(Rcorr_invs_sel_sig2[ix])
  corr_invs_sel_labs.append(Rcorr_invs_sel_labs2[ix])
  corr_invs_sel_lay.append(Rcorr_invs_sel_lay2[ix])


for ix in range (0, len(PMinvs_sel_sup1)):
  #if (corr_invs_sel_supp1[ix] <= 20):
  #   continue
  Minvs_sel_supp.append(PMinvs_sel_sup1[ix])
  Minvs_sel_neus.append(PMinvs_sel_neus1[ix])
  Minvs_sel_sig.append(PMinvs_sel_sig1[ix])
  Minvs_sel_labs.append(PMinvs_sel_cl1[ix])
  Minvs_sel_lay.append(PMinvs_sel_lay1[ix])



for ix in range (0, len(PMinvs_sel_sup2)):
  Minvs_sel_supp.append(PMinvs_sel_sup2[ix])
  Minvs_sel_neus.append(PMinvs_sel_neus2[ix])
  Minvs_sel_sig.append(PMinvs_sel_sig2[ix])
  Minvs_sel_labs.append(PMinvs_sel_cl2[ix])
  Minvs_sel_lay.append(PMinvs_sel_lay2[ix])




for ix in range (0, len(corr_invs_sel_supp)-1):
    for iy in range(ix +1, len(corr_invs_sel_supp)):
        if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
          temp = corr_invs_sel_supp[iy]
          corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
          corr_invs_sel_supp[ix] = temp
          temp = corr_invs_sel_neus[iy]
          corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
          corr_invs_sel_neus[ix] = temp
          temp = corr_invs_sel_sig[iy]
          corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
          corr_invs_sel_sig[ix] = temp
          temp = corr_invs_sel_labs[iy]
          corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
          corr_invs_sel_labs[ix] = temp
          temp = corr_invs_sel_lay[iy]
          corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
          corr_invs_sel_lay[ix] = temp


for indx in range (0, len(corr_invs_sel_neus)):
      Cneu_ids = []
      for indx1 in range (0, len(corr_invs_sel_neus[indx])):
        Cneu_ids.append(-1)
        Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
      Cneuron_ids.append(Cneu_ids)
      C_neuron_ids.append(corr_invs_sel_neus[indx])


for indx in range (0, len(corr_invs_sel_sig)):
      Cneuron_sig.append(corr_invs_sel_sig[indx])
      Cneuron_cl.append(corr_invs_sel_labs[indx])
      Cneuron_lay.append(corr_invs_sel_lay[indx])

print("\n CORRECT PATTERNS\n")
for indx in range (0, len(Cneuron_cl)):
  print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])


for ix in range (0, len(Minvs_sel_supp)-1):
    for iy in range(ix +1, len(Minvs_sel_supp)):
        if (Minvs_sel_supp[iy] > Minvs_sel_supp[ix]):
          temp = Minvs_sel_supp[iy]
          Minvs_sel_supp[iy] = Minvs_sel_supp[ix]
          Minvs_sel_supp[ix] = temp
          temp = Minvs_sel_neus[iy]
          Minvs_sel_neus[iy] = Minvs_sel_neus[ix]
          Minvs_sel_neus[ix] = temp
          temp = Minvs_sel_sig[iy]
          Minvs_sel_sig[iy] = Minvs_sel_sig[ix]
          Minvs_sel_sig[ix] = temp
          temp = Minvs_sel_labs[iy]
          Minvs_sel_labs[iy] = Minvs_sel_labs[ix]
          Minvs_sel_labs[ix] = temp
          temp = Minvs_sel_lay[iy]
          Minvs_sel_lay[iy] = Minvs_sel_lay[ix]
          Minvs_sel_lay[ix] = temp


for indx in range (0, len(Minvs_sel_neus)):
      MCneu_ids = []
      for indx1 in range (0, len(Minvs_sel_neus[indx])):
        MCneu_ids.append(-1)
        MCneu_ids.append(Minvs_sel_neus[indx][indx1])
      MCneuron_ids.append(MCneu_ids)
      MC_neuron_ids.append(Minvs_sel_neus[indx])


for indx in range (0, len(Minvs_sel_sig)):
      MCneuron_sig.append(Minvs_sel_sig[indx])
      MCneuron_cl.append(Minvs_sel_labs[indx])
      MCneuron_lay.append(Minvs_sel_lay[indx])

print("\n MIS-CLASSIFICATION PATTERNS\n")
for indx in range (0, len(MCneuron_cl)):
  print(MCneuron_cl[indx],Minvs_sel_supp[indx],MCneuron_lay[indx],MC_neuron_ids[indx],MCneuron_sig[indx])

x = copy.deepcopy(Pval_X)
cnt = 0
correct = 0

labels = (model.predict(x)).argmax(axis=1)
ideals = Pval_Y




true_positives = 0
true_negatives = 0
false_positives = 0
false_negatives = 0
cnt_not_fnd = 0
broke = 0
pois_pat = 0


PASS = 0
PASS_bef = 0
FAIL = 0
FAIL_bef = 0

clean_pass = 0
clean_fail = 0
pois_pass = 0
pois_fail = 0


for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
    cnt = cnt + 1
    image = x[inp_cnt]
    label = labels[inp_cnt]

   # inp = image
   # inc_layer = 'dense'  #layer name, get it from the model summary
   # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

    #layer_vals = inc_suff[0]
    #suff = []



    img = np.zeros((32,32,3),dtype=float)
    for ix in range(0,32):
      for iy in range(0,32):
        for iz in range(0,3):
          img[ix][iy][iz] = (float(image[ix][iy][iz]))

    image_array = np.zeros((1,32,32,3),dtype=float)
    image_array[0]=img
    img_mod = np.expand_dims(img,axis=0)


    inp = image
    inc_layer = 'dense'  #layer name, get it from the model summary
    inc_suff = fingerprint_suffix_vals(inp, inc_layer)
    layer_vals1 = inc_suff[0]
    suff = []

    inp = image
    inc_layer = 'activation_4'  #layer name, get it from the model summary
    inc_suff = fingerprint_suffix_vals(inp, inc_layer)
    layer_vals2 = inc_suff[0]


    layer_vals3 = np.array([])



    max_lab7 = False
    match1 = -1
    Same = True
    match1 = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,MCneuron_lay,MCneuron_ids,MCneuron_sig)
    print("MATCH MIS-CLASS:", match1)
    if (len(match1) == 0):
      cnt_not_fnd = cnt_not_fnd + 1
      new_lbl = labels[inp_cnt]
    else:
      match = -1
      match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig)
      if (len(match) == 0):
      #  cnt_not_fnd = cnt_not_fnd + 1
        new_lbl = labels[inp_cnt]
      else:
        if (Cneuron_lay[match[0]] == 3):
          if (len(match) > 1):
            new_lbl = Cneuron_cl[match[1]]
          else:
            new_lbl = labels[inp_cnt]
        else:
          new_lbl = Cneuron_cl[match[0]]

        Same = True
        prev_lab = -1
        for indx in range(0,len(match)):
          print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
          if (Cneuron_lay[match[indx]] ==3):
            continue
          if (prev_lab != -1 and Cneuron_cl[match[indx]] != prev_lab):
            Same=False
          prev_lab = Cneuron_cl[match[indx]]




    if (new_lbl == ideals[inp_cnt]):
      PASS = PASS + 1
      if (labels[inp_cnt] != ideals[inp_cnt]):
        correct = correct + 1
        if (max_lab7 == True):
          pois_pat = pois_pat + 1
    else:
      if (Same == False):
        print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
      FAIL = FAIL + 1
      if (labels[inp_cnt] == ideals[inp_cnt]):
        broke = broke + 1

print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
print('CORRECTED:', float(correct/cnt)*100)
print('BROKEN:', float(broke/cnt)*100)
print('POIS PAT',pois_pat)
print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )

strat1c_pois_time = (time.time() - strat1c_start_pois_time)/ len(x)

print("STRAT 1C RUNTIME:", (strat1c_pois_time + strat1c_time)/2.0)


Streaming output truncated to the last 5000 lines.
LAYER,LABEL,SUPP 1 4 1
OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL: 0 6 [699, 1558] 5
MATCH MIS-CLASS: [0, 1]
LAYER,LABEL,SUPP 2 3 3
LAYER,LABEL,SUPP 1 0 2
OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL: 0 5 [535, 726] 3
MATCH MIS-CLASS: [0, 1]
LAYER,LABEL,SUPP 1 4 5
LAYER,LABEL,SUPP 2 5 4
OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL: 0 1 [281, 339] 4
MATCH MIS-CLASS: [0, 1]
LAYER,LABEL,SUPP 1 4 2
LAYER,LABEL,SUPP 2 1 2
OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL: 0 3 [585, 827] 4
MATCH MIS-CLASS: [1]
LAYER,LABEL,SUPP 1 9 3
LAYER,LABEL,SUPP 2 7 1
OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL: 0 0 [429, 1105] 9
MATCH MIS-CLASS: [0, 1]
LAYER,LABEL,SUPP 2 4 10
MATCH MIS-CLASS: [0, 2]
LAYER,LABEL,SUPP 2 9 10
LAYER,LABEL,SUPP 1 4 4
MATCH MIS-CLASS: [0, 1]
LAYER,LABEL,SUPP 1 4 55
MATCH MIS-CLASS: [0, 1]
LAYER,LABEL,SUPP 2 4 10
LAYER,LABEL,SUPP 1 8 3
OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL: 0 0 [144, 417] 4
MATCH MIS-CLASS: [0, 1]
LAYER,LABEL,SUPP 2 4 10
MATCH MIS-CLA

In [ ]:
##### STOP HERE OLD RESULTS

In [ ]:

# #### GUESSING THE IDEAL LABELS BASED ON PATTERNS
# neuron_ids =[]
# inc_neuron_ids=[]
# neuron_sig = []

# Cneuron_ids =[]
# C_neuron_ids=[]
# Cneuron_sig = []
# Cneuron_cl = []
# Cneuron_lay = []

# corr_invs_sel_supp = []
# corr_invs_sel_neus = []
# corr_invs_sel_sig = []
# corr_invs_sel_labs = []
# corr_invs_sel_lay = []

# for ix in range (0, len(corr_invs_sel_supp1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   corr_invs_sel_supp.append(corr_invs_sel_supp1[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus1[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig1[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs1[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay1[ix])

# # for ix in range (0, len(corr_invs_sel_supp1a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp1a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus1a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig1a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs1a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay1a[ix])

# for ix in range (0, len(corr_invs_sel_supp2)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp2[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus2[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig2[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs2[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay2[ix])

# # for ix in range (0, len(corr_invs_sel_supp2a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp2a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus2a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig2a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs2a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay2a[ix])

# for ix in range (0, len(corr_invs_sel_supp3)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp3[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus3[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig3[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs3[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay3[ix])

# # for ix in range (0, len(corr_invs_sel_supp3a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp3a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus3a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig3a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs3a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay3a[ix])


# for ix in range (0, len(corr_invs_sel_supp)-1):
#     for iy in range(ix +1, len(corr_invs_sel_supp)):
#         if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
#           temp = corr_invs_sel_supp[iy]
#           corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
#           corr_invs_sel_supp[ix] = temp
#           temp = corr_invs_sel_neus[iy]
#           corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
#           corr_invs_sel_neus[ix] = temp
#           temp = corr_invs_sel_sig[iy]
#           corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
#           corr_invs_sel_sig[ix] = temp
#           temp = corr_invs_sel_labs[iy]
#           corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
#           corr_invs_sel_labs[ix] = temp
#           temp = corr_invs_sel_lay[iy]
#           corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
#           corr_invs_sel_lay[ix] = temp


# for indx in range (0, len(corr_invs_sel_neus)):
#       Cneu_ids = []
#       for indx1 in range (0, len(corr_invs_sel_neus[indx])):
#         Cneu_ids.append(-1)
#         Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
#       Cneuron_ids.append(Cneu_ids)
#       C_neuron_ids.append(corr_invs_sel_neus[indx])


# for indx in range (0, len(corr_invs_sel_sig)):
#       Cneuron_sig.append(corr_invs_sel_sig[indx])
#       Cneuron_cl.append(corr_invs_sel_labs[indx])
#       Cneuron_lay.append(corr_invs_sel_lay[indx])

# print("\n CORRECT PATTERNS\n")
# for indx in range (0, len(Cneuron_cl)):
#   print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])


# x = copy.deepcopy(test_X_pois)
# cnt = 0
# correct = 0

# labels = (model.predict(x)).argmax(axis=1)
# ideals = testFULL_Y






# true_positives = 0
# true_negatives = 0
# false_positives = 0
# false_negatives = 0
# cnt_not_fnd = 0
# broke = 0
# pois_pat = 0


# PASS = 0
# PASS_bef = 0
# FAIL = 0
# FAIL_bef = 0

# clean_pass = 0
# clean_fail = 0
# pois_pass = 0
# pois_fail = 0


# for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
#     cnt = cnt + 1
#     image = x[inp_cnt]
#     label = labels[inp_cnt]

#    # inp = image
#    # inc_layer = 'dense'  #layer name, get it from the model summary
#    # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

#     #layer_vals = inc_suff[0]
#     #suff = []



#     img = np.zeros((28,28),dtype=float)
#     for ix in range(0,28):
#       for iy in range(0,28):
#           img[ix][iy] = (float(image[ix][iy][0]))

#     image_array = np.zeros((1,28,28),dtype=float)
#     image_array[0]=img
#     img_mod = np.expand_dims(img,axis=0)


#     inp = image
#     inc_layer = 'dense_1'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals1 = inc_suff[0]
#     suff = []

#     inp = image
#     inc_layer = 'activation_3'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals2 = inc_suff[0]

#     inp = image
#     inc_layer = 'dense_2'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals3 = inc_suff[0]
#     suff = []


#     max_lab7 = False
#     match = -1
#     match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig)
#     print("MATCH:", match)
#     if (len(match) == 0):
#       cnt_not_fnd = cnt_not_fnd + 1
#       new_lbl = labels[inp_cnt]
#     else:
#       if (Cneuron_lay[match[0]] == 3):
#         max_lab7 = True
#         if (len(match) > 1):
#           new_lbl = Cneuron_cl[match[1]]
#         else:
#           new_lbl = labels[inp_cnt]
#       else:
#         new_lbl = Cneuron_cl[match[0]]






#     if (new_lbl == ideals[inp_cnt]):
#       PASS = PASS + 1
#       if (labels[inp_cnt] != ideals[inp_cnt]):
#         correct = correct + 1
#         if (max_lab7 == True):
#           pois_pat = pois_pat + 1
#     else:
#       for indx in range(0,len(match)):
#          print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
#       print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
#       FAIL = FAIL + 1
#       if (labels[inp_cnt] == ideals[inp_cnt]):
#         broke = broke + 1
#       #print("BROKE: OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)


# print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

# print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
# print('CORRECTED:', float(correct/cnt)*100)
# print('BROKEN:', float(broke/cnt)*100)
# print('POIS PAT',pois_pat)
# print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )


In [ ]:

# #### GUESSING THE IDEAL LABELS BASED ON PATTERNS
# neuron_ids =[]
# inc_neuron_ids=[]
# neuron_sig = []

# Cneuron_ids =[]
# C_neuron_ids=[]
# Cneuron_sig = []
# Cneuron_cl = []
# Cneuron_lay = []

# corr_invs_sel_supp = []
# corr_invs_sel_neus = []
# corr_invs_sel_sig = []
# corr_invs_sel_labs = []
# corr_invs_sel_lay = []

# for ix in range (0, len(corr_invs_sel_supp1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   corr_invs_sel_supp.append(corr_invs_sel_supp1[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus1[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig1[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs1[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay1[ix])

# # for ix in range (0, len(corr_invs_sel_supp1a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp1a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus1a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig1a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs1a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay1a[ix])

# for ix in range (0, len(corr_invs_sel_supp2)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp2[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus2[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig2[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs2[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay2[ix])

# # for ix in range (0, len(corr_invs_sel_supp2a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp2a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus2a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig2a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs2a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay2a[ix])

# for ix in range (0, len(corr_invs_sel_supp3)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp3[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus3[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig3[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs3[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay3[ix])

# # for ix in range (0, len(corr_invs_sel_supp3a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp3a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus3a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig3a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs3a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay3a[ix])


# for ix in range (0, len(corr_invs_sel_supp)-1):
#     for iy in range(ix +1, len(corr_invs_sel_supp)):
#         if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
#           temp = corr_invs_sel_supp[iy]
#           corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
#           corr_invs_sel_supp[ix] = temp
#           temp = corr_invs_sel_neus[iy]
#           corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
#           corr_invs_sel_neus[ix] = temp
#           temp = corr_invs_sel_sig[iy]
#           corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
#           corr_invs_sel_sig[ix] = temp
#           temp = corr_invs_sel_labs[iy]
#           corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
#           corr_invs_sel_labs[ix] = temp
#           temp = corr_invs_sel_lay[iy]
#           corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
#           corr_invs_sel_lay[ix] = temp


# for indx in range (0, len(corr_invs_sel_neus)):
#       Cneu_ids = []
#       for indx1 in range (0, len(corr_invs_sel_neus[indx])):
#         Cneu_ids.append(-1)
#         Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
#       Cneuron_ids.append(Cneu_ids)
#       C_neuron_ids.append(corr_invs_sel_neus[indx])


# for indx in range (0, len(corr_invs_sel_sig)):
#       Cneuron_sig.append(corr_invs_sel_sig[indx])
#       Cneuron_cl.append(corr_invs_sel_labs[indx])
#       Cneuron_lay.append(corr_invs_sel_lay[indx])

# print("\n CORRECT PATTERNS\n")
# for indx in range (0, len(Cneuron_cl)):
#   print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])


# x = copy.deepcopy(test_X_pois)
# cnt = 0
# correct = 0

# labels = (model.predict(x)).argmax(axis=1)
# ideals = testFULL_Y






# true_positives = 0
# true_negatives = 0
# false_positives = 0
# false_negatives = 0
# cnt_not_fnd = 0
# broke = 0
# pois_pat = 0


# PASS = 0
# PASS_bef = 0
# FAIL = 0
# FAIL_bef = 0

# clean_pass = 0
# clean_fail = 0
# pois_pass = 0
# pois_fail = 0


# for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
#     cnt = cnt + 1
#     image = x[inp_cnt]
#     label = labels[inp_cnt]

#    # inp = image
#    # inc_layer = 'dense'  #layer name, get it from the model summary
#    # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

#     #layer_vals = inc_suff[0]
#     #suff = []



#     img = np.zeros((28,28),dtype=float)
#     for ix in range(0,28):
#       for iy in range(0,28):
#           img[ix][iy] = (float(image[ix][iy][0]))

#     image_array = np.zeros((1,28,28),dtype=float)
#     image_array[0]=img
#     img_mod = np.expand_dims(img,axis=0)


#     inp = image
#     inc_layer = 'dense_1'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals1 = inc_suff[0]
#     suff = []

#     inp = image
#     inc_layer = 'activation_3'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals2 = inc_suff[0]

#     inp = image
#     inc_layer = 'dense_2'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals3 = inc_suff[0]
#     suff = []


#     max_lab7 = False
#     match = -1
#     match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig,support=corr_invs_sel_supp,supp_thres = 50)
#     print("MATCH:", match)
#     if (len(match) == 0):
#       cnt_not_fnd = cnt_not_fnd + 1
#       new_lbl = labels[inp_cnt]
#     else:
#       if (Cneuron_lay[match[0]] == 3):
#         max_lab7 = True
#         if (len(match) > 1):
#           new_lbl = Cneuron_cl[match[1]]
#         else:
#           new_lbl = labels[inp_cnt]
#       else:
#         new_lbl = Cneuron_cl[match[0]]






#     if (new_lbl == ideals[inp_cnt]):
#       PASS = PASS + 1
#       if (labels[inp_cnt] != ideals[inp_cnt]):
#         correct = correct + 1
#         if (max_lab7 == True):
#           pois_pat = pois_pat + 1
#     else:
#       for indx in range(0,len(match)):
#          print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
#       print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
#       FAIL = FAIL + 1
#       if (labels[inp_cnt] == ideals[inp_cnt]):
#         broke = broke + 1
#       #print("BROKE: OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)


# print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

# print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
# print('CORRECTED:', float(correct/cnt)*100)
# print('BROKEN:', float(broke/cnt)*100)
# print('POIS PAT',pois_pat)
# print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )

In [ ]:

# #### GUESSING THE IDEAL LABELS BASED ON PATTERNS
# neuron_ids =[]
# inc_neuron_ids=[]
# neuron_sig = []

# Cneuron_ids =[]
# C_neuron_ids=[]
# Cneuron_sig = []
# Cneuron_cl = []
# Cneuron_lay = []

# corr_invs_sel_supp = []
# corr_invs_sel_neus = []
# corr_invs_sel_sig = []
# corr_invs_sel_labs = []
# corr_invs_sel_lay = []

# for ix in range (0, len(corr_invs_sel_supp1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   corr_invs_sel_supp.append(corr_invs_sel_supp1[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus1[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig1[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs1[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay1[ix])

# # for ix in range (0, len(corr_invs_sel_supp1a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp1a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus1a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig1a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs1a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay1a[ix])

# for ix in range (0, len(corr_invs_sel_supp2)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp2[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus2[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig2[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs2[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay2[ix])

# # for ix in range (0, len(corr_invs_sel_supp2a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp2a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus2a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig2a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs2a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay2a[ix])

# for ix in range (0, len(corr_invs_sel_supp3)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp3[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus3[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig3[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs3[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay3[ix])

# # for ix in range (0, len(corr_invs_sel_supp3a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp3a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus3a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig3a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs3a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay3a[ix])


# for ix in range (0, len(corr_invs_sel_supp)-1):
#     for iy in range(ix +1, len(corr_invs_sel_supp)):
#         if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
#           temp = corr_invs_sel_supp[iy]
#           corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
#           corr_invs_sel_supp[ix] = temp
#           temp = corr_invs_sel_neus[iy]
#           corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
#           corr_invs_sel_neus[ix] = temp
#           temp = corr_invs_sel_sig[iy]
#           corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
#           corr_invs_sel_sig[ix] = temp
#           temp = corr_invs_sel_labs[iy]
#           corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
#           corr_invs_sel_labs[ix] = temp
#           temp = corr_invs_sel_lay[iy]
#           corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
#           corr_invs_sel_lay[ix] = temp


# for indx in range (0, len(corr_invs_sel_neus)):
#       Cneu_ids = []
#       for indx1 in range (0, len(corr_invs_sel_neus[indx])):
#         Cneu_ids.append(-1)
#         Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
#       Cneuron_ids.append(Cneu_ids)
#       C_neuron_ids.append(corr_invs_sel_neus[indx])


# for indx in range (0, len(corr_invs_sel_sig)):
#       Cneuron_sig.append(corr_invs_sel_sig[indx])
#       Cneuron_cl.append(corr_invs_sel_labs[indx])
#       Cneuron_lay.append(corr_invs_sel_lay[indx])

# print("\n CORRECT PATTERNS\n")
# for indx in range (0, len(Cneuron_cl)):
#   print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])


# x = copy.deepcopy(test_X_pois)
# cnt = 0
# correct = 0

# labels = (model.predict(x)).argmax(axis=1)
# ideals = testFULL_Y




# true_positives = 0
# true_negatives = 0
# false_positives = 0
# false_negatives = 0
# cnt_not_fnd = 0
# broke = 0
# pois_pat = 0


# PASS = 0
# PASS_bef = 0
# FAIL = 0
# FAIL_bef = 0

# clean_pass = 0
# clean_fail = 0
# pois_pass = 0
# pois_fail = 0


# for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
#     cnt = cnt + 1
#     image = x[inp_cnt]
#     label = labels[inp_cnt]

#    # inp = image
#    # inc_layer = 'dense'  #layer name, get it from the model summary
#    # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

#     #layer_vals = inc_suff[0]
#     #suff = []



#     img = np.zeros((28,28),dtype=float)
#     for ix in range(0,28):
#       for iy in range(0,28):
#           img[ix][iy] = (float(image[ix][iy][0]))

#     image_array = np.zeros((1,28,28),dtype=float)
#     image_array[0]=img
#     img_mod = np.expand_dims(img,axis=0)


#     inp = image
#     inc_layer = 'dense_1'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals1 = inc_suff[0]
#     suff = []

#     inp = image
#     inc_layer = 'activation_3'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals2 = inc_suff[0]

#     inp = image
#     inc_layer = 'dense_2'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals3 = inc_suff[0]
#     suff = []


#     max_lab7 = False
#     match = -1
#     match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig,support=corr_invs_sel_supp,supp_thres = 50)
#     #print("MATCH:", match)
#     if (len(match) == 0):
#       cnt_not_fnd = cnt_not_fnd + 1
#       new_lbl = labels[inp_cnt]
#     else:
#       labs = []
#       votes = []
#       new_lbl = -1
#       for indx in range(0,len(match)):
#         l = Cneuron_cl[match[indx]]
#         v = 0
#         for indx1 in range(0,len(labs)):
#           if (labs[indx1] == l):
#             votes[indx1] += 1
#             break
#         if (v == 0):
#           labs.append(l)
#           votes.append(v+1)

#       max = -1
#       max_indx = -1
#       for indx in range(0,len(votes)):
#         if (votes[indx] > max):
#           max = votes[indx]
#           max_indx = indx

#       if (max_indx == -1):
#         new_lbl = labels[inp_cnt]
#       else:
#         new_lbl = labs[max_indx]


#     # match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig)
#     # print("MATCH:", match)
#     # if (len(match) == 0):
#     #   cnt_not_fnd = cnt_not_fnd + 1
#     #   new_lbl = labels[inp_cnt]
#     # else:
#     #   if (Cneuron_lay[match[0]] == 3):
#     #     max_lab7 = True
#     #     if (len(match) > 1):
#     #       new_lbl = Cneuron_cl[match[1]]
#     #     else:
#     #       new_lbl = labels[inp_cnt]
#     #   else:
#     #     new_lbl = Cneuron_cl[match[0]]
#     #   SAME = False
#     #   for indx in range(0,len(match)):
#     #      print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
#     #      if ()



#     if (new_lbl == ideals[inp_cnt]):
#       PASS = PASS + 1
#       if (labels[inp_cnt] != ideals[inp_cnt]):
#         correct = correct + 1
#         if (max_lab7 == True):
#           pois_pat = pois_pat + 1
#     else:
#       for indx in range(0,len(match)):
#           print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
#       print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
#       FAIL = FAIL + 1
#       if (labels[inp_cnt] == ideals[inp_cnt]):
#         broke = broke + 1
#       #print("BROKE: OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)


# print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

# print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
# print('CORRECTED:', float(correct/cnt)*100)
# print('BROKEN:', float(broke/cnt)*100)
# print('POIS PAT',pois_pat)
# print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )


In [ ]:

# #### GUESSING THE IDEAL LABELS BASED ON PATTERNS
# neuron_ids =[]
# inc_neuron_ids=[]
# neuron_sig = []

# Cneuron_ids =[]
# C_neuron_ids=[]
# Cneuron_sig = []
# Cneuron_cl = []
# Cneuron_lay = []

# corr_invs_sel_supp = []
# corr_invs_sel_neus = []
# corr_invs_sel_sig = []
# corr_invs_sel_labs = []
# corr_invs_sel_lay = []

# for ix in range (0, len(corr_invs_sel_supp1)):
#   #if (corr_invs_sel_supp1[ix] <= 20):
#   #   continue
#   corr_invs_sel_supp.append(corr_invs_sel_supp1[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus1[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig1[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs1[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay1[ix])

# # for ix in range (0, len(corr_invs_sel_supp1a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp1a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus1a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig1a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs1a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay1a[ix])

# for ix in range (0, len(corr_invs_sel_supp2)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp2[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus2[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig2[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs2[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay2[ix])

# # for ix in range (0, len(corr_invs_sel_supp2a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp2a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus2a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig2a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs2a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay2a[ix])

# for ix in range (0, len(corr_invs_sel_supp3)):
#   corr_invs_sel_supp.append(corr_invs_sel_supp3[ix])
#   corr_invs_sel_neus.append(corr_invs_sel_neus3[ix])
#   corr_invs_sel_sig.append(corr_invs_sel_sig3[ix])
#   corr_invs_sel_labs.append(corr_invs_sel_labs3[ix])
#   corr_invs_sel_lay.append(corr_invs_sel_lay3[ix])

# # for ix in range (0, len(corr_invs_sel_supp3a)):
# #   corr_invs_sel_supp.append(corr_invs_sel_supp3a[ix])
# #   corr_invs_sel_neus.append(corr_invs_sel_neus3a[ix])
# #   corr_invs_sel_sig.append(corr_invs_sel_sig3a[ix])
# #   corr_invs_sel_labs.append(corr_invs_sel_labs3a[ix])
# #   corr_invs_sel_lay.append(corr_invs_sel_lay3a[ix])


# for ix in range (0, len(corr_invs_sel_supp)-1):
#     for iy in range(ix +1, len(corr_invs_sel_supp)):
#         if (corr_invs_sel_supp[iy] > corr_invs_sel_supp[ix]):
#           temp = corr_invs_sel_supp[iy]
#           corr_invs_sel_supp[iy] = corr_invs_sel_supp[ix]
#           corr_invs_sel_supp[ix] = temp
#           temp = corr_invs_sel_neus[iy]
#           corr_invs_sel_neus[iy] = corr_invs_sel_neus[ix]
#           corr_invs_sel_neus[ix] = temp
#           temp = corr_invs_sel_sig[iy]
#           corr_invs_sel_sig[iy] = corr_invs_sel_sig[ix]
#           corr_invs_sel_sig[ix] = temp
#           temp = corr_invs_sel_labs[iy]
#           corr_invs_sel_labs[iy] = corr_invs_sel_labs[ix]
#           corr_invs_sel_labs[ix] = temp
#           temp = corr_invs_sel_lay[iy]
#           corr_invs_sel_lay[iy] = corr_invs_sel_lay[ix]
#           corr_invs_sel_lay[ix] = temp


# for indx in range (0, len(corr_invs_sel_neus)):
#       Cneu_ids = []
#       for indx1 in range (0, len(corr_invs_sel_neus[indx])):
#         Cneu_ids.append(-1)
#         Cneu_ids.append(corr_invs_sel_neus[indx][indx1])
#       Cneuron_ids.append(Cneu_ids)
#       C_neuron_ids.append(corr_invs_sel_neus[indx])


# for indx in range (0, len(corr_invs_sel_sig)):
#       Cneuron_sig.append(corr_invs_sel_sig[indx])
#       Cneuron_cl.append(corr_invs_sel_labs[indx])
#       Cneuron_lay.append(corr_invs_sel_lay[indx])

# print("\n CORRECT PATTERNS\n")
# for indx in range (0, len(Cneuron_cl)):
#   print(Cneuron_cl[indx],corr_invs_sel_supp[indx],Cneuron_lay[indx],C_neuron_ids[indx],Cneuron_sig[indx])



# gen_data = test_X_pois
# gen_labels = test_Y
# actuals_gen = (model.predict(gen_data)).argmax(axis=1)

# x = copy.deepcopy(gen_data)
# cnt = 0
# correct = 0

# labels = actuals_gen #actuals_gen
# ideals = gen_labels #gen_labels




# true_positives = 0
# true_negatives = 0
# false_positives = 0
# false_negatives = 0
# cnt_not_fnd = 0
# broke = 0
# pois_pat = 0


# PASS = 0
# PASS_bef = 0
# FAIL = 0
# FAIL_bef = 0

# clean_pass = 0
# clean_fail = 0
# pois_pass = 0
# pois_fail = 0


# for inp_cnt in range(0,len(x)): # x is the list of images in the dataset used to extract the mis-classification pattern
#     cnt = cnt + 1
#     image = x[inp_cnt]
#     label = labels[inp_cnt]

#    # inp = image
#    # inc_layer = 'dense'  #layer name, get it from the model summary
#    # inc_suff = fingerprint_suffix_vals(inp, inc_layer)

#     #layer_vals = inc_suff[0]
#     #suff = []



#     img = np.zeros((28,28),dtype=float)
#     for ix in range(0,28):
#       for iy in range(0,28):
#           img[ix][iy] = (float(image[ix][iy][0]))

#     image_array = np.zeros((1,28,28),dtype=float)
#     image_array[0]=img
#     img_mod = np.expand_dims(img,axis=0)


#     inp = image
#     inc_layer = 'dense_1'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals1 = inc_suff[0]
#     suff = []

#     inp = image
#     inc_layer = 'activation_3'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals2 = inc_suff[0]

#     inp = image
#     inc_layer = 'dense_2'  #layer name, get it from the model summary
#     inc_suff = fingerprint_suffix_vals(inp, inc_layer)
#     layer_vals3 = inc_suff[0]
#     suff = []


#     max_lab7 = False
#     match = -1
#     Same = True
#     match = check_pattern_inter_lays(layer_vals1,layer_vals2,layer_vals3,Cneuron_lay,Cneuron_ids,Cneuron_sig)
#     print("MATCH:", match)
#     if (len(match) == 0):
#       cnt_not_fnd = cnt_not_fnd + 1
#       new_lbl = labels[inp_cnt]
#     else:
#       if (Cneuron_lay[match[0]] == 3):
#         max_lab7 = True
#         if (len(match) > 1):
#           new_lbl = Cneuron_cl[match[1]]
#         else:
#           new_lbl = labels[inp_cnt]
#       else:
#         new_lbl = Cneuron_cl[match[0]]

#       prev_cls = -1
#       for indx in range(0,len(match)):
#          print("LAYER,LABEL,SUPP", Cneuron_lay[match[indx]],Cneuron_cl[match[indx]], corr_invs_sel_supp[match[indx]])
#          if (Cneuron_cl[match[indx]] != prev_cls and (Same == True)):
#            Same = False
#            prev_cls = Cneuron_cl[match[indx]]





#     if (new_lbl == ideals[inp_cnt]):
#       PASS = PASS + 1
#       if (labels[inp_cnt] != ideals[inp_cnt]):
#   #      print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
#         correct = correct + 1
#         if (max_lab7 == True):
#           pois_pat = pois_pat + 1
#     else:
#       if (Same == False):
#         print("OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)
#       FAIL = FAIL + 1
#       if (labels[inp_cnt] == ideals[inp_cnt]):
#         broke = broke + 1
#       #print("BROKE: OLD LABEL, IDEAL LABEL, MATCH,NEW LABEL:", labels[inp_cnt], ideals[inp_cnt],match,new_lbl)


# print("\n DISTILLATION BASED ON PATTERNS FOR IDEAL LABEL:")

# print('TOTAL GUESSED BASED ON PATTERNs :',float((cnt - cnt_not_fnd)/cnt)*100)
# print('CORRECTED:', float(correct/cnt)*100)
# print('BROKEN:', float(broke/cnt)*100)
# print('POIS PAT',pois_pat)
# print("PASS:", PASS, ", FAIL:", FAIL, ", OVERALL ACCURACY with monitor:", (PASS/(PASS+FAIL)) * 100 )
